# Smart nanogrid optimisation visualisation

## 1. Import libraries

In [1]:
import numpy as np
import os
import argparse
import time

import pandas as pd
import plotly
import plotly.express as px
from plotly.subplots import make_subplots, go
import plotly.io as pio

import json
import datetime

## 2. Specify plotting information

In [2]:
pd.options.plotting.backend = "plotly"

Plotly templates to use: 'ggplot2', 'seaborn', 'simple_white', 'plotly', 'plotly_white', 'plotly_dark', 'presentation', 'xgridoff', 'ygridoff', 'gridon', 'none'

In [3]:
pio.templates.default = "plotly_white"

In [4]:
pd.set_option('display.max_columns', None)

Available pattern shapes to use in plotting: "", "/", "\\", "x", "|", "-", ".", "+"

Named CSS colors to use in plotting: `aliceblue, antiquewhite, aqua, aquamarine, azure, beige, bisque, black, blanchedalmond, blue, blueviolet, brown, burlywood, cadetblue, chartreuse, chocolate, coral, cornflowerblue, cornsilk, crimson, cyan, darkblue, darkcyan, darkgoldenrod, darkgrey, darkgreen, darkkhaki, darkmagenta, darkolivegreen, darkorange, darkorchid, darkred, darksalmon, darkseagreen, darkslateblue, darkslategrey, darkturquoise, darkviolet, deeppink, deepskyblue, dimgrey, dodgerblue, firebrick, floralwhite, forestgreen, fuchsia, gainsboro, ghostwhite, gold, goldenrod, grey, green, greenyellow, honeydew, hotpink, indianred, indigo, ivory, khaki, lavender, lavenderblush, lawngreen, lemonchiffon, lightblue, lightcoral, lightcyan, lightgoldenrodyellow, lightgrey, lightgreen, lightpink, lightsalmon, lightseagreen, lightskyblue, lightslategrey, lightsteelblue, lightyellow, lime, limegreen, linen, magenta, maroon, mediumaquamarine, mediumblue, mediumorchid, mediumpurple, mediumseagreen, mediumslateblue, mediumspringgreen, mediumturquoise, mediumvioletred, midnightblue, mintcream, mistyrose, moccasin, navajowhite, navy, oldlace, olive, olivedrab, orange, orangered, orchid, palegoldenrod, palegreen, paleturquoise, palevioletred, papayawhip, peachpuff, peru, pink, plum, powderblue, purple, red, rosybrown, royalblue, rebeccapurple, saddlebrown, salmon, sandybrown, seagreen, seashell, sienna, silver, skyblue, slateblue, slategrey, snow, springgreen, steelblue, tan, teal, thistle, tomato, turquoise, violet, wheat, white, whitesmoke, yellow, yellowgreen`

## 3. Specify model information

In [5]:
# Existing optimisation models:
model_names = ['model1', 'model2', 'model3', 'model4']
# model_names = ['model4']
model = 'model4'
# End-to-Requested State of Charge ratio modes
# end2req_soc_modes = ['5+- margin', 'requested']
if not os.path.exists(f"plots/{model}"):
    os.mkdir(f"plots/{model}")

## 4. Specify data files information

Initial data

In [6]:
initial_data_directory = 'data'

In [7]:
building_data_file = 'building_data_2016.csv'
model_parameters_file = 'components_data.csv'
charging_station_file = 'parking_lot_data.csv'
solar_production_file = 'pv_data.csv'
market_data_file = 'market_data.csv'

Optimised data

In [8]:
# results, results_required
results_directory = 'optimisation_results/results'

In [9]:
optimised_charging_schedule_file = 'optimal_ev_charging_schedule.xlsx'
nanogrid_optimised_variables_file = 'nanogrid_optimisation_results.xlsx'

## 5. Load and process data for training results visualisation

In [10]:
temp_data = dict()

Initial data

In [11]:
file_path = f"{initial_data_directory}/{building_data_file}"
temp_data_building = pd.read_csv(file_path, sep=";", header=[0], index_col=[0], skiprows=1, parse_dates=True, decimal=',')

In [12]:
file_path = f"{initial_data_directory}/{market_data_file}"
temp_data_market = pd.read_csv(file_path, sep=";", header=[0], index_col=[0], skiprows=1, decimal=',')
temp_data_market = temp_data_market[['tariff']].reset_index(drop=True)

In [13]:
file_path = f"{initial_data_directory}/{model_parameters_file}"
temp_data['parameters'] = pd.read_csv(file_path, sep=";", header=0, index_col=[1], decimal=',')

In [14]:
file_path = f"{initial_data_directory}/{charging_station_file}"
temp_data['parking_lot'] = pd.read_csv(file_path, sep=";", header=[0, 1], index_col=[0], skiprows=1, decimal='.')

In [15]:
file_path = f"{initial_data_directory}/{solar_production_file}"
temp_data['pv_system'] = pd.read_csv(file_path, sep=";", header=[0], index_col=[0], skiprows=1, 
                                     parse_dates=True, decimal=',')

Optimised data

In [16]:
file_path = f"{results_directory}/{model}/{optimised_charging_schedule_file}"
temp_data['charging_schedule'] = pd.read_excel(file_path, sheet_name=None)

In [17]:
file_path = f"{results_directory}/{model}/{nanogrid_optimised_variables_file}"
temp_data['optimised_variables'] = pd.read_excel(file_path, sheet_name=None)

In [18]:
grid_tariff_high = 0.029199
grid_tariff_low = 0.013272
energy_tariff_high = 0.285854
energy_tariff_low = 0.168150
res_incentive = 0.014

high_tariff = grid_tariff_high + energy_tariff_high + res_incentive
low_tariff = grid_tariff_low + energy_tariff_low + res_incentive

del grid_tariff_high, energy_tariff_high, grid_tariff_low, energy_tariff_low, res_incentive

## 6. Process data for visualisation

##### Initial data - Building

In [19]:
temp_data_building = temp_data_building.reset_index(drop=True)
temp_data_building

DATE_2016  2016
0         1.1.16. 0:00  12.8
1         1.1.16. 0:15  13.0
2         1.1.16. 0:30  12.8
3         1.1.16. 0:45  13.2
4         1.1.16. 1:00  13.4
...                ...   ...
35035  30.12.16. 22:45  14.8
35036  30.12.16. 23:00  14.8
35037  30.12.16. 23:15  14.6
35038  30.12.16. 23:30  14.2
35039  30.12.16. 23:45  13.8

[35040 rows x 2 columns]

In [20]:
building_df = temp_data_building[['2016']].copy()
del temp_data_building

In [21]:
def generate_heatmap_from_data(data_df, plot_title='', plot_xlabel='', plot_ylabel='', plot_fontsize=11, plot_figuresize=(20,20), plot_cmap='turbo'):
    M = data_df.max()
    N = 96  # Every hour has 4 15min interval (00:00, 00:15, 00:30, 00:45) 4*24h=96 15min intervals
    n_days = len(data_df) / N
    
    heatmap_df = pd.DataFrame()
    i = 0

    while i < len(data_df):
        temp_df = data_df.iloc[i:i+N][data_df.columns[0]].to_frame(name=int(i/N)).reset_index(drop=True)
        heatmap_df = pd.concat([heatmap_df, temp_df], axis="columns")
        i = i + N
    
    heatmap_df.index = heatmap_df.index.map(lambda x: x*15/60)
    
    pv_fig = px.imshow(heatmap_df, color_continuous_scale='spectral_r', origin='lower', aspect='auto')
    pv_fig.update_yaxes(tickformat=" ,~", nticks=24, range=[0, 24*4], dtick=1, ticks='outside',
                        tickvals=[i/4 for i in range(0, 96, 4)], 
                        ticktext=[f'{int(i/4)}:00' for i in range(0, 96, 4)],
                        title='<b>Hour in a day</b>')
    
    pv_fig.update_xaxes(griddash="dot", range=[0, 365], ticks='outside', title='<b>Day in a year</b>',
                        tickvals=[i for i in range(0, 365, 14)],
                        ticktext=[str(i+1) for i in range(0, 365, 14)])
    
    plot_width = 950
    plot_height = 550
    pv_fig.update_layout(height=plot_height, width=plot_width, font_size=16,
                         coloraxis=dict(colorbar=dict(len=1.05, thickness=20, 
                                                      title=dict(text='<b>Building Power Demand [kW]</b>',
                                                                 side='right'))),
                         font_family="Computer Modern Roman")
#     pv_fig.show()
    if not os.path.exists("plots/heatmaps"):
        os.mkdir("plots/heatmaps")

    pv_fig.write_image("plots/heatmaps/heatmap_building.png")

In [22]:
generate_heatmap_from_data(building_df)

In [23]:
building_df.columns = ['Building Demand']
building_df['Day'] = building_df.index // 96

building_df

Building Demand  Day
0                 12.8    0
1                 13.0    0
2                 12.8    0
3                 13.2    0
4                 13.4    0
...                ...  ...
35035             14.8  364
35036             14.8  364
35037             14.6  364
35038             14.2  364
35039             13.8  364

[35040 rows x 2 columns]

In [24]:
building_df.loc[building_df['Building Demand'] == building_df['Building Demand'].max(), :]

Building Demand  Day
1772            118.0   18

In [25]:
building_demand = dict()
i = 0
max_day = building_df['Day'].max() + 1
while i < max_day:
    building_demand[i] = building_df.loc[building_df['Day'] == i, :].reset_index(drop=True)
    i = i + 1

# del building_df

In [26]:
building_demand[0]

Building Demand  Day
0              12.8    0
1              13.0    0
2              12.8    0
3              13.2    0
4              13.4    0
..              ...  ...
91             13.0    0
92             13.2    0
93             13.2    0
94             13.0    0
95             13.0    0

[96 rows x 2 columns]

##### Initial data - relative solar production

In [27]:
temp_pv = temp_data['pv_system'].reset_index(drop=True)

heatmap_pv_df = pd.DataFrame()
i = 0

while i < len(temp_pv):
    temp_df = temp_pv.iloc[i:i+96].reset_index(drop=True)
    temp_df.columns = [int(i/96)]
    heatmap_pv_df = pd.concat([heatmap_pv_df, temp_df], axis="columns")
    i = i + 96
heatmap_pv_df.index = heatmap_pv_df.index.map(lambda x: x*15/60)

del temp_pv

In [28]:
heatmap_pv_df

0    1    2    3    4    5    6    7    8    9    10   11   12   13   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.50   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.75   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

       14   15   16   17   18   19   20   21   22   23   24   25   26   27   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.50   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.75   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

       28   29   30   31   32   33   34   35   36   37   38   39   40   41   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.50   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.75   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

       42   43   44   45   46   47   48   49   50   51   52   53   54   55   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.50   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.75   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

       56   57   58   59   60   61   62   63   64   65   66   67   68   69   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0

In [29]:
pv_fig = px.imshow(heatmap_pv_df, color_continuous_scale='solar', origin='lower', aspect='auto')
pv_fig.update_yaxes(tickformat=" ,~", nticks=24, range=[0, 24*4], dtick=1, ticks='outside',
                    tickvals=[i/4 for i in range(0, 96, 4)],
                    ticktext=[f'{int(i/4)}:00' for i in range(0, 96, 4)],
                    title='<b>Hour in a day</b>')

pv_fig.update_xaxes(griddash="dot", range=[0, 365], ticks='outside', title='<b>Day in a year</b>',
                    tickvals=[i for i in range(0, 365, 14)],
                    ticktext=[str(i+1) for i in range(0, 365, 14)])

plot_width = 950
plot_height = 550
pv_fig.update_layout(height=plot_height, width=plot_width, font_size=16,
                     coloraxis=dict(colorbar=dict(len=1.05, thickness=20, 
                                                  title=dict(text='<b>Relative PV System Production</b>',
                                                             side='right'))),
                     font_family="Computer Modern Roman")
# pv_fig.show()
if not os.path.exists("plots/heatmaps"):
    os.mkdir("plots/heatmaps")

pv_fig.write_image("plots/heatmaps/heatmap_solar.png")

##### Initial data - charging station initial info

In [30]:
charger_number = [charger for charger, variable in temp_data['parking_lot'].columns]
charger_set = set(charger_number)
chargers = list(charger_set)
chargers.sort()
print(chargers)

['Lot1', 'Lot2', 'Lot3', 'Lot4', 'Lot5', 'Lot6', 'Lot7', 'Lot8']


In [31]:
initial_data = pd.DataFrame()
charger_occupancy = pd.DataFrame()
vehicle_capacities = pd.DataFrame()

for charger_index, charger in enumerate(chargers):
    temp_lot = temp_data['parking_lot'][charger].fillna(0)
    temp_lot.index = temp_lot.index - 1
    
    temp_df = pd.DataFrame(temp_lot['available'])
    temp_df.columns = ['Charger Occupation State']
    temp_df['Charger ID'] = charger_index
    temp_df['Day'] = temp_df.index // 96
    temp_df['Charger Occupation State'] = temp_df['Charger Occupation State'] - temp_lot['departure']
    charger_occupancy = pd.concat([charger_occupancy, temp_df])
    
    temp_df = pd.DataFrame(temp_lot['capacity']).fillna(0)
    temp_df.columns = ['Vehicle Capacities']
    temp_df['Charger ID'] = charger_index
    temp_df['Vehicle Capacities'] = temp_df['Vehicle Capacities'] - temp_lot['departure'] * temp_df['Vehicle Capacities']
    temp_df['Day'] = temp_df.index // 96
    vehicle_capacities = pd.concat([vehicle_capacities, temp_df])
    
    arrivals = []
    departures = []
    
    for i in temp_lot.index:
        if temp_lot['arrival'][i] == 1:
            arrivals.append(i)
        if temp_lot['departure'][i] == 1:
            departures.append(i)
    
    vehicle_counter = 0
    old_arrival_day = 0
    for vehicle, arrival in enumerate(arrivals):
        df = pd.DataFrame()
        arrival_day = int(arrival / 96)
        departure_day = int(departures[vehicle] / 96)
        
        df['Arrival'] = [arrival%96]
        df['Departure'] = departures[vehicle] - arrival_day*96
        
        df['Day'] = arrival_day

        df['Charger ID'] = str(charger_index)

        df['EV Capacity'] = temp_lot.iloc[arrival]['capacity']

        df['Initial State of Charge'] = temp_lot.iloc[arrival]['initial']
        df['Requested State of Charge'] = temp_lot.iloc[arrival]['end']

        if arrival_day != old_arrival_day:
            vehicle_counter = 0
            old_arrival_day = arrival_day
        df['Vehicle ID'] = vehicle_counter
        if arrival_day == old_arrival_day:
            vehicle_counter = vehicle_counter + 1
        
        initial_data = pd.concat([initial_data.loc[:], df]).reset_index(drop=True)
        
        if arrival_day != departure_day:
            occupancy = departure_day - arrival_day
            
            for day in range(occupancy):
                df['Arrival'] = -((96 - arrival%96)%96) - 96*day
                df['Departure'] = departures[vehicle]  - arrival_day*96 - 96*(day + 1)
                df['Day'] = arrival_day + 1 + day
                df['Vehicle ID'] = -1 - day
                initial_data = pd.concat([initial_data.loc[:], df]).reset_index(drop=True)
                

initial_data = initial_data[['Arrival', 'Departure', 'EV Capacity', 'Initial State of Charge', 
                             'Requested State of Charge', 'Vehicle ID', 'Charger ID', 'Day']]

del df, arrivals, arrival, departures, temp_lot, vehicle, charger_index, charger, i, temp_df, arrival_day
del departure_day, vehicle_counter

In [32]:
charger_occupancy_days = dict()
i = 0
max_day = initial_data['Day'].max() + 1
while i < max_day:
    charger_occupancy_days[i] = charger_occupancy.loc[charger_occupancy['Day'] == i]
    charger_occupancy_days[i].index = charger_occupancy_days[i].index % 96
    i = i + 1

del charger_occupancy

In [33]:
vehicle_capacities_days = dict()
i = 0
max_day = initial_data['Day'].max() + 1
while i < max_day:
    vehicle_capacities_days[i] = vehicle_capacities.loc[vehicle_capacities['Day'] == i]
    vehicle_capacities_days[i].index = vehicle_capacities_days[i].index % 96
    i = i + 1

del vehicle_capacities

In [34]:
initial_data_days = dict()
i = 0
max_day = initial_data['Day'].max() + 1
while i < max_day:
    initial_data_days[i] = initial_data.loc[initial_data['Day'] == i, :].reset_index(drop=True)
    i = i + 1

del initial_data

In [35]:
number_of_chargers = len(chargers)

In [36]:
def plot_single_day_initial_info(day, model=''):
    subplot_fig = make_subplots(rows=number_of_chargers, cols=1, shared_xaxes=True, vertical_spacing=0.03)
    
    for charger_id in range(number_of_chargers):
            counter = number_of_chargers - charger_id
            charger = counter - 1
            subplot_fig.add_scatter(y=[0], x=[0], row=counter, col=1, name='', line_width=0, mode='lines',
                                    marker=dict(size=0.1, symbol='circle'), showlegend=False)
            subplot_fig.add_annotation(x=92, y=1.2, text=f'<i>Charger {charger+1}</i>', textangle=0, opacity=0.9, 
                                   row=charger_id+1, col=1, font_size=14, showarrow=False, font_color='grey')

    max_ev_cap = vehicle_capacities_days[day]['Vehicle Capacities'].max()
    if len(initial_data_days[day]) > 0:
        all_vehicles = list(initial_data_days[day].index)
        vehicle_from_yesterday = False
        vehicle_counter = 0
        old_charger = -1
        for v_id in all_vehicles:
            charger_id = int(initial_data_days[day].loc[v_id, 'Charger ID'])
            counter = number_of_chargers - charger_id
            charger = counter - 1

            arr = int(initial_data_days[day].loc[v_id, 'Arrival'])
            dep = int(initial_data_days[day].loc[v_id, 'Departure'])

            ev_cap_text = str(initial_data_days[day].loc[v_id, 'EV Capacity'])
            
            if old_charger!=charger_id:
                vehicle_from_yesterday = False
            
            if initial_data_days[day].loc[v_id, 'Vehicle ID'] < 0:
                vehicle_from_yesterday = True
                old_charger = charger_id
                vehicle_counter = 0
            elif initial_data_days[day].loc[v_id, 'Vehicle ID'] == 0 and not vehicle_from_yesterday:
                vehicle_from_yesterday = False
                old_charger = charger_id
                vehicle_counter = 0
            else:
                vehicle_counter = vehicle_counter + 1
                old_charger = charger_id
                vehicle_from_yesterday = False
            
            if vehicle_counter == 0:
                subplot_fig.add_scatter(line_shape='hv',
                                        y=charger_occupancy_days[day].loc[charger_occupancy_days[day]['Charger ID']==charger_id,'Charger Occupation State'], 
                                        row=counter, col=1, name=f'Occupied', 
                                        x=[i for i in range(0, 96, 1)],
                                        fillpattern=dict(shape='/', fgcolor='rgba(71, 164, 235, 0.5)', fgopacity=0.5),
                                        fillcolor=f'rgba(71, 164, 235, 0.4)', 
                                        line_width=0, fill='tozeroy', 
                                        legendgroup='Charger occupancy', showlegend=(not v_id), 
                                        legendgrouptitle=dict(text='<em>Charger</em>'))
                subplot_fig.add_scatter(line_shape='hv',
                                        x=[i for i in range(0, 96, 1)],
                                        y=vehicle_capacities_days[day].loc[vehicle_capacities_days[day]['Charger ID']==charger_id,'Vehicle Capacities']/max_ev_cap, 
                                        row=counter, col=1, name='Vehicle Capacity [kWh]',
                                        fillcolor=f'rgba(71, 164, 235, 0.5)', 
                                        line_width=0, fill='tozeroy', legendgroup='Charger occupancy',
                                        showlegend=(not v_id))
                
            x=[initial_data_days[day]['Departure'].iloc[v_id]]
            y=[initial_data_days[day]['Requested State of Charge'].iloc[v_id]]
            subplot_fig.add_bar(x=x, 
                                row=counter, col=1,
                                y=y, 
                                name=f'Requested - on departure',
                                width=0.8, marker=dict(color='teal', opacity=0.8, line_width=0), 
                                legendgroup='State of Charge', showlegend=(not v_id),
                                legendgrouptitle=dict(text='<em>State of Charge</em>'))
            subplot_fig.add_scatter(x=x, 
                                row=counter, col=1, mode='markers',
                                y=y, 
                                marker=dict(color='teal', opacity=0.8, line_width=0), 
                                legendgroup='State of Charge', showlegend=False,
                                legendgrouptitle=dict(text='State of Charge'))

            x=[initial_data_days[day]['Arrival'].iloc[v_id]]
            y=[initial_data_days[day]['Initial State of Charge'].iloc[v_id]]
            subplot_fig.add_bar(x=x, 
                                row=counter, col=1,
                                y=y, 
                                name=f'Initial - on arrival', width=0.8, 
                                marker=dict(color='crimson', opacity=0.8, line_width=0), 
                                legendgroup='State of Charge', showlegend=(not v_id))
            subplot_fig.add_scatter(x=x, 
                                row=counter, col=1, mode='markers',
                                y=y, 
                                marker=dict(color='crimson', opacity=0.8, line_width=0), 
                                legendgroup='State of Charge', showlegend=False)

            if dep > 96 and arr > 88:
                subplot_fig.add_annotation(x=(max(arr, 0)+min(dep, 96))/2, y=0.5, text=f'<i>{ev_cap_text}</i>', textangle=-90, opacity=0.9, 
                                           font_size=11, row=counter, col=1, showarrow=False, font_color='white')
            elif dep < 8 and arr <= 0:
                subplot_fig.add_annotation(x=(max(arr, 0)+min(dep, 96))/2, y=0.5, text=f'<i>{ev_cap_text}</i>', textangle=-90, opacity=0.9, 
                                           font_size=11, row=counter, col=1, showarrow=False, font_color='white')
            else:
                subplot_fig.add_annotation(x=(max(arr, 0)+min(dep, 96))/2, y=0.2, text=f'<i>{ev_cap_text}</i>', textangle=0, opacity=0.9, 
                                           font_size=14, row=counter, col=1, showarrow=False, font_color='white')

            subplot_fig.add_shape(type='line', x0=arr, x1=arr, y0=0, y1=1, layer='above',
                                  line_color='crimson', line_width=1.5, row=counter, col=1)
            subplot_fig.add_shape(type='line', x0=dep, x1=dep, y0=0, y1=1, layer='above',
                                  line_color='teal', line_width=1.5, row=counter, col=1)
        del arr, dep, ev_cap_text

    subplot_fig.add_annotation(x=-0.08, y=0.5, text="<b>State of Charge</b>", textangle=-90, xref="paper", yref="paper", font_size=15, showarrow=False)
    subplot_fig.add_annotation(x=0.5, y=-0.07, text="<b>Timestep in a Day (h)</b>", textangle=0, xref="paper", yref="paper", font_size=15, showarrow=False)

    if len(initial_data_days[day]) == number_of_chargers:
        max_timestep = max(int(initial_data_days[day].Departure.max()), 100)
        min_timestep = min(int(initial_data_days[day].Arrival.min() - initial_data_days[day].Arrival.min()%2 - 2), 0)
    else:
        max_timestep = 100
        min_timestep = 0
    
    # subplot_fig.update_layout(title="Initial Model Info", barmode='overlay')
    subplot_fig.update_layout(title="", barmode='overlay')
    subplot_fig.update_xaxes(griddash="dot", range=[-0.2, 96.2], 
                             tickvals=[i for i in range(min_timestep, max_timestep, 4)],
                             ticktext=[str(int(i/4)%24) for i in range(min_timestep, max_timestep, 4)])

    # For plot export: w(1280)xh(720), w(1920)xh(1080)
    # For better overview in jupyter: w(850)xh(650)
    plot_width = 950
    plot_height = 850

    subplot_fig.update_yaxes(tickformat=" ,~%", nticks=5, range=[0, 1.2], dtick=0.25)
    subplot_fig.update_layout(height=plot_height, width=plot_width, 
                              title=dict(xanchor="center", x=0.43, font_size=24, y=0.9),
                              showlegend=True, 
                              legend=dict(groupclick='togglegroup', x=0.5, orientation='h', font_size=17,
                                          yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'), 
                              font_family="Computer Modern Roman")

#     subplot_fig.show()
    if not os.path.exists(f"plots"):
        os.mkdir(f"plots")

    subplot_fig.write_image(f"plots/initial_info_day_{day}.png")

    del charger_id, counter, charger, max_ev_cap, max_timestep, min_timestep, plot_width, plot_height

In [37]:
def plot_days_range_initial_info(first_day=0, last_day=0, model=''):
    for d in range(first_day, last_day + 1, 1):
        plot_single_day_initial_info(day=d, model=model)
    print('------------------------------------\n'
          'Finished plotting days initial info.\n'
          '------------------------------------\n')

##### Prediction data - charging schedule

In [38]:
soc_predictions = pd.DataFrame()
for charger_index, charger in enumerate(chargers):
    temp_lot = pd.DataFrame(temp_data['charging_schedule']['SOE_ev_relative'][[charger]])
    temp_lot.columns = ['Vehicle State of Charge']
    temp_lot['Charger ID'] = charger_index
    temp_lot['Day'] = temp_lot.index // 96
    soc_predictions = pd.concat([soc_predictions, temp_lot])

del temp_lot

In [39]:
vehicle_state_of_charge = dict()
i = 0
max_day = soc_predictions['Day'].max() + 1
while i < max_day:
    vehicle_state_of_charge[i] = soc_predictions.loc[soc_predictions['Day'] == i, :].reset_index(drop=True)
    i = i + 1

del soc_predictions

##### Prediction data - charging station power predictions

In [40]:
ev_power_predictions = pd.DataFrame()
for charger_index, charger in enumerate(chargers):
    if model == 'model2' or model == 'model4':
        tdf = temp_data['charging_schedule']['P_ev_ch'][[charger]] - temp_data['charging_schedule']['P_ev_ds'][[charger]]
        temp_lot = pd.DataFrame(tdf)
    else:
        tdf = temp_data['charging_schedule']['P_ev_ch'][[charger]]
        temp_lot = pd.DataFrame(tdf)
    temp_lot.columns = ['Charger Power Value']
    temp_lot.replace(0, np.nan, inplace=True)
    temp_lot['Charger ID'] = charger_index
    temp_lot['Day'] = temp_lot.index // 96
    ev_power_predictions = pd.concat([ev_power_predictions, temp_lot])

del temp_lot, tdf

In [41]:
charger_power_predictions = dict()
i = 0
max_day = ev_power_predictions['Day'].max() + 1
while i < max_day:
    charger_power_predictions[i] = ev_power_predictions.loc[ev_power_predictions['Day'] == i, :].reset_index(drop=True)
    i = i + 1

del ev_power_predictions

In [42]:
def plot_single_day_power_predictions(day, model=''):
    day_length = len(vehicle_state_of_charge[day]) / number_of_chargers

    subplot_fig = make_subplots(
        rows=8,
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.02,
        specs=[[{'secondary_y': True}]]*8
    )
    
    for charger_id in range(number_of_chargers):
        counter = number_of_chargers - charger_id
        charger = counter - 1
        subplot_fig.add_scatter(y=[0], x=[0], row=counter, col=1, name='', line_width=0, mode='lines',
                                marker=dict(size=0.1, symbol='circle'), showlegend=False)
        subplot_fig.add_annotation(x=92, y=1.18, text=f'<i>Charger {charger+1}</i>', textangle=0, opacity=0.9, 
                               row=charger_id+1, col=1, font_size=14, showarrow=False, font_color='grey')

    charger_patterns = ['', '/', '\\', '+']
    if len(initial_data_days[day]) > 0:
        all_vehicles = list(initial_data_days[day].index)
        vehicle_from_yesterday = False
        vehicle_counter = 0
        old_charger = -1
        for v_id in all_vehicles:
            charger_id = int(initial_data_days[day].loc[v_id, 'Charger ID'])
            counter = number_of_chargers - charger_id
            charger = counter - 1

            arr = int(initial_data_days[day].loc[v_id, 'Arrival'])
            dep = int(initial_data_days[day].loc[v_id, 'Departure'])
            
            if old_charger!=charger_id:
                vehicle_from_yesterday = False
            
            if initial_data_days[day].loc[v_id, 'Vehicle ID'] < 0:
                vehicle_from_yesterday = True
                old_charger = charger_id
                vehicle_counter = 0
            elif initial_data_days[day].loc[v_id, 'Vehicle ID'] == 0 and not vehicle_from_yesterday:
                vehicle_from_yesterday = False
                old_charger = charger_id
                vehicle_counter = 0
            else:
                vehicle_counter = vehicle_counter + 1
                old_charger = charger_id
                vehicle_from_yesterday = False
            
            if vehicle_counter == 0:
                psoc = vehicle_state_of_charge[day].loc[vehicle_state_of_charge[day]['Charger ID']==charger_id,'Vehicle State of Charge']
                ppowers = charger_power_predictions[day].loc[charger_power_predictions[day]['Charger ID']==charger_id,'Charger Power Value']

                subplot_fig.add_scatter(y=psoc, line_shape='linear', row=counter, col=1, name='Value at timestep end', mode='markers+lines',
                                        marker=dict(size=5, symbol='circle'), line=dict(color='darkturquoise'), 
                                        showlegend=(not v_id), secondary_y=False,
                                        legendgrouptitle=dict(text='<em>Predicted State of Charge</em>'), legendgroup='Predicted Charger SOC')
                subplot_fig.add_bar(y=psoc, row=counter, col=1, legendgroup='Predicted Charger SOC', showlegend=False, 
                                        marker=dict(color='darkturquoise', opacity=0.45, line_width=0))
            
            x=[initial_data_days[day]['Departure'].iloc[v_id]]
            y=[initial_data_days[day]['Requested State of Charge'].iloc[v_id]]
            subplot_fig.add_bar(x=x, 
                                row=counter, col=1,
                                y=y, 
                                name=f'Requested - on departure',
                                width=0.5, marker=dict(color='teal', opacity=0.8, line_width=0), 
                                legendgroup='State of Charge', showlegend=(not v_id),
                                legendgrouptitle=dict(text='<em>State of Charge</em>'))
            subplot_fig.add_scatter(x=x, 
                                row=counter, col=1, mode='markers',
                                y=y, 
                                marker=dict(color='teal', opacity=0.8, line_width=0), 
                                legendgroup='State of Charge', showlegend=False,
                                legendgrouptitle=dict(text='State of Charge'))

            x=[initial_data_days[day]['Arrival'].iloc[v_id]]
            y=[initial_data_days[day]['Initial State of Charge'].iloc[v_id]]
            subplot_fig.add_bar(x=x, 
                                row=counter, col=1,
                                y=y, 
                                name=f'Initial - on arrival', width=0.5, 
                                marker=dict(color='crimson', opacity=0.8, line_width=0), 
                                legendgroup='State of Charge', showlegend=(not v_id))
            subplot_fig.add_scatter(x=x, 
                                row=counter, col=1, mode='markers',
                                y=y, 
                                marker=dict(color='crimson', opacity=0.8, line_width=0), 
                                legendgroup='State of Charge', showlegend=False)
            
            if vehicle_counter == 0:
                subplot_fig.add_scatter(y=ppowers, line_shape='linear', row=counter, col=1, name=f'Value at current timestep', mode='markers',
                                        marker=dict(size=5, symbol='square'), line=dict(color='darkorange'), 
                                        showlegend=(not v_id), secondary_y=True,
                                        legendgrouptitle=dict(text='<em>Power</em>'), legendgroup='Charger Power')
                subplot_fig.add_bar(y=ppowers, row=counter, col=1, legendgroup='Charger Power', showlegend=False, width=0.2,
                                    secondary_y=True, marker=dict(color='darkorange', opacity=0.45, line_width=0))

    subplot_fig.add_annotation(x=-0.1, y=0.75, yanchor='middle', text="<b>State of Charge</b>", textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
    subplot_fig.add_annotation(x=-0.1, y=0.25, yanchor='middle', text="<b>State of Charge</b>", textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
    subplot_fig.add_annotation(x=1.02, y=0.75, text="<b>Power [kW]</b>", textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
    subplot_fig.add_annotation(x=1.02, y=0.25, text="<b>Power [kW]</b>", textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
    subplot_fig.add_annotation(x=12/26, y=-0.05, text="<b>Timestep (Hour) in a Day</b>", textangle=0, xref="paper", yref="paper", font_size=14, showarrow=False)

    if len(initial_data_days[day]) == number_of_chargers:
        max_timestep = max(int(initial_data_days[day].Departure.max()), 100)
        min_timestep = min(int(initial_data_days[day].Arrival.min() - initial_data_days[day].Arrival.min()%2 - 2), 0)
    else:
        max_timestep = 100
        min_timestep = 0
    # Predicted State of Charge with Action and Power Values
    subplot_fig.update_layout(title="",
                              yaxis=dict(title=''), barmode='overlay')
    subplot_fig.update_xaxes(tickformat='', griddash="dot", range=[-0.4, day_length+0.4],
                             tickvals=[i for i in range(min_timestep, max_timestep, 4)],
                             ticktext=[str(int(i/4)%24) for i in range(min_timestep, max_timestep, 4)])

    # For plot export: w(1280)xh(720), w(1920)xh(1080)
    # For better overview in jupyter: w(850)xh(650)
    plot_width = 990
    plot_height = 1290
    
    if model == 'model2' or model == 'model4':
        min_power = -23.6
        min_soc = -1.18
    else:
        min_power = 0
        min_soc = 0
    
    fontsize=12

    subplot_fig.update_layout(height=plot_height, width=plot_width, title=dict(xanchor="center", x=0.5, font_size=24, y=0.92), 
                              showlegend=True, legend=dict(groupclick='togglegroup', x=0.5, orientation='h', 
                                                           yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'), 
                              margin=dict(autoexpand=True),
                              xaxis4=dict(showticklabels=True, title=dict(text="<b>Timestep (Hour) in a Day</b>")), font_family="Computer Modern Roman",
                              yaxis=dict(tickformat=" ,~%", nticks=5, range=[min_soc, 1.18], dtick=0.2, rangemode='nonnegative', tickfont=dict(size=fontsize)),
                              yaxis2=dict(tickformat=" ,~", nticks=5, range=[min_power, 23.6], dtick=4, tickfont=dict(size=fontsize)),
                              yaxis3=dict(tickformat=" ,~%", nticks=5, range=[min_soc, 1.18], dtick=0.2, rangemode='nonnegative', tickfont=dict(size=fontsize)),
                              yaxis4=dict(tickformat=" ,~", nticks=5, range=[min_power, 23.6], dtick=4, tickfont=dict(size=fontsize)),
                              yaxis5=dict(tickformat=" ,~%", nticks=5, range=[min_soc, 1.18], dtick=0.2, rangemode='nonnegative', tickfont=dict(size=fontsize)),
                              yaxis6=dict(tickformat=" ,~", nticks=5, range=[min_power, 23.6], dtick=4, tickfont=dict(size=fontsize)),
                              yaxis7=dict(tickformat=" ,~%", nticks=5, range=[min_soc, 1.18], dtick=0.2, rangemode='nonnegative', tickfont=dict(size=fontsize)),
                              yaxis8=dict(tickformat=" ,~", nticks=5, range=[min_power, 23.6], dtick=4, tickfont=dict(size=fontsize)),
                              yaxis9=dict(tickformat=" ,~%", nticks=5, range=[min_soc, 1.18], dtick=0.2, rangemode='nonnegative', tickfont=dict(size=fontsize)),
                              yaxis10=dict(tickformat=" ,~", nticks=5, range=[min_power, 23.6], dtick=4, tickfont=dict(size=fontsize)),
                              yaxis11=dict(tickformat=" ,~%", nticks=5, range=[min_soc, 1.18], dtick=0.2, rangemode='nonnegative', tickfont=dict(size=fontsize)),
                              yaxis12=dict(tickformat=" ,~", nticks=5, range=[min_power, 23.6], dtick=4, tickfont=dict(size=fontsize)),
                              yaxis13=dict(tickformat=" ,~%", nticks=5, range=[min_soc, 1.18], dtick=0.2, rangemode='nonnegative', tickfont=dict(size=fontsize)),
                              yaxis14=dict(tickformat=" ,~", nticks=5, range=[min_power, 23.6], dtick=4, tickfont=dict(size=fontsize)),
                              yaxis15=dict(tickformat=" ,~%", nticks=5, range=[min_soc, 1.18], dtick=0.2, rangemode='nonnegative', tickfont=dict(size=fontsize)),
                              yaxis16=dict(tickformat=" ,~", nticks=5, range=[min_power, 23.6], dtick=4, tickfont=dict(size=fontsize)))

#     subplot_fig.show()
    if not os.path.exists(f"plots/{model}"):
        os.mkdir(f"plots/{model}")

    subplot_fig.write_image(f"plots/{model}/{model}_prediction_powers_day_{day}.png")

#     del psoc, charger_id, counter, charger, arr, dep, max_timestep, plot_width, plot_height

In [43]:
def plot_days_range_power_predictions(first_day=0, last_day=0, model=''):
    for d in range(first_day, last_day + 1, 1):
        plot_single_day_power_predictions(day=d, model=model)
    print('------------------------------------\n'
          'Finished plotting days predicted powers.\n'
          '------------------------------------\n')

##### Prediction data - solar production heatmap

In [44]:
temp_pv = temp_data['optimised_variables']['15-min optimal data for 1 year'][['P_pv']].reset_index(drop=True)

heatmap_pv_df = pd.DataFrame()
i = 0

while i < len(temp_pv):
    temp_df = temp_pv.iloc[i:i+96].reset_index(drop=True)
    temp_df.columns = [int(i/96)]
    
    heatmap_pv_df = pd.concat([heatmap_pv_df, temp_df], axis="columns")
    i = i + 96
heatmap_pv_df.index = heatmap_pv_df.index.map(lambda x: x*15/60)
heatmap_pv_df

0    1    2    3    4    5    6    7    8    9    10   11   12   13   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.50   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.75   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

       14   15   16   17   18   19   20   21   22   23   24   25   26   27   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.50   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.75   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

       28   29   30   31   32   33   34   35   36   37   38   39   40   41   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.50   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.75   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

       42   43   44   45   46   47   48   49   50   51   52   53   54   55   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.50   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.75   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23.75  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

       56   57   58   59   60   61   62   63   64   65   66   67   68   69   \
0.00   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
0.25   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0

##### Prediction data - battery heatmap

In [45]:
temp_bess = temp_data['optimised_variables']['15-min optimal data for 1 year'][['E_battery']].reset_index(drop=True)

heatmap_bess_df = pd.DataFrame()
i = 0

while i < len(temp_bess):
    temp_df = temp_bess.iloc[i:i+96].reset_index(drop=True)
    temp_df.columns = [int(i/96)]
    
    heatmap_bess_df = pd.concat([heatmap_bess_df, temp_df], axis="columns")
    i = i + 96
heatmap_bess_df.index = heatmap_bess_df.index.map(lambda x: x*15/60)
heatmap_bess_df

0           1           2           3           4           5    \
0.00    37.320401  119.041044  103.616206  125.616647  119.041044  137.181361   
0.25    49.907755  126.295505  109.684142  133.376924  126.295505  145.688731   
0.50    62.495109  133.549966  115.752077  141.137201  133.549966  152.818602   
0.75    75.082463  140.804428  121.820013  148.897478  140.804428  159.568472   
1.00    87.669817  148.058889  127.887948  156.657755  148.058889  165.463343   
...           ...         ...         ...         ...         ...         ...   
22.75   82.768737   73.276530   86.815262   82.768737   93.932009  237.257930   
23.00   90.023199   79.344465   94.575539   90.023199  102.581880  238.791026   
23.25   97.277660   85.412400  102.335816   97.277660  111.231750  240.324122   
23.50  104.532121   91.480336  110.096093  104.532121  119.881620  241.857218   
23.75  111.786582   97.548271  117.856370  111.786582  128.531491  243.342813   

              6           7           8           9           10          11   \
0.00   244.828409  129.260732  122.218086  106.311362  128.676671  129.260732   
0.25   245.503150  137.301323  129.716936  114.285657  136.757037  137.301323   
0.50   245.292624  145.341914  137.215785  122.259951  144.837403  145.341914   
0.75   245.292624  153.382505  144.714634  130.234246  152.917769  153.382505   
1.00   245.668057  161.423096  152.213483  138.208540  160.998135  161.423096   
...           ...         ...         ...         ...         ...         ...   
22.75   89.057776   84.723840   66.439889   88.274842   89.057776   68.766527   
23.00   97.098367   92.222689   74.414184   96.355207   97.098367   75.001025   
23.25  105.138958   99.721539   82.388478  104.435573  105.138958   82.597914   
23.50  113.179549  107.220388   90.362773  112.515939  113.179549   90.194804   
23.75  121.220141  114.719237   98.337068  120.596305  121.220141   97.791693   

              12          13          14          15          16          17   \
0.00   105.388583  119.041044  137.400183  112.048939  116.786578  129.260732   
0.25   112.985472  126.295505  146.066885  120.157295  124.168524  137.301323   
0.50   120.582362  133.549966  154.733588  128.265652  131.550470  145.341914   
0.75   128.179251  140.804428  163.400291  136.374008  138.932416  153.382505   
1.00   135.776141  148.058889  172.066994  144.482365  146.314362  161.423096   
...           ...         ...         ...         ...         ...         ...   
22.75   82.768737   94.066669   71.507156   79.876848   89.057776   65.429213   
23.00   90.023199  102.733372   79.615513   87.258794   97.098367   73.450376   
23.25   97.277660  111.400074   87.723869   94.640740  105.138958   81.614038   
23.50  104.532121  120.066777   95.832226  102.022686  113.179549   89.920200   
23.75  111.786582  128.733480  103.940582  109.404632  121.220141   98.368863   

              18          19          20          21          22          23   \
0.00   106.817525  121.401832  124.700508  146.914296  116.174273  122.218086   
0.25   116.386507  131.329816  132.425125  156.312854  124.536581  129.716936   
0.50   125.955488  141.257799  140.149742  165.711412  132.898888  137.215785   
0.75   135.524470  151.185783  147.874360  175.109969  141.261196  144.714634   
1.00   145.093452  161.113766  155.598977  184.508527  149.623503  152.213483   
...           ...         ...         ...         ...         ...         ...   
22.75   71.761915   86.077420   99.921508   74.362735   84.723840   96.875494   
23.00   81.689898   93.802038  109.320066   82.725043   92.222689  105.893299   
23.25   91.617882  101.526655  118.718623   91.087350   99.721539  114.911105   
23.50  101.545865  109.251273  128.117181   99.449658  107.220388  123.928911   
23.75  111.473849  116.975890  137.515739  107.811965  114.719237  132.946717   

              24          25          26          27          28          29   \
0.00   141.964523  116.992761  101.896541

In [46]:
pv_fig = px.imshow(heatmap_bess_df, color_continuous_scale='thermal', origin='lower', aspect='auto')
pv_fig.update_yaxes(tickformat=" ,~", nticks=24, range=[0, 24*4], dtick=1, ticks='outside',
                    tickvals=[i/4 for i in range(0, 96, 4)],
                    ticktext=[f'{int(i/4)}:00' for i in range(0, 96, 4)],
                    title=dict(font_size=22, text='<b>Hour in a day</b>'))

pv_fig.update_xaxes(griddash="dot", range=[0, 365], ticks='outside', title=dict(font_size=22, text='<b>Day in a year</b>'),
                    tickvals=[i for i in range(0, 365, 14)],
                    ticktext=[str(i+1) for i in range(0, 365, 14)])

plot_width = 950
plot_height = 550
pv_fig.update_layout(height=plot_height, width=plot_width, font_size=16,
                     coloraxis=dict(colorbar=dict(len=1.05, thickness=20, 
                                                  title=dict(text='<b>Battery Energy [kWh]</b>', font_size=22,
                                                             side='right'))),
                     font_family="Computer Modern Roman")
# pv_fig.show()
if not os.path.exists(f"plots/{model}"):
    os.mkdir(f"plots/{model}")

pv_fig.write_image(f"plots/{model}/{model}_heatmap_battery_energy.png")

##### Prediction data - Battery charging power

In [47]:
temp_bess_ch = temp_data['optimised_variables']['15-min optimal data for 1 year']['P_battery_ch']
temp_bess_ds = temp_data['optimised_variables']['15-min optimal data for 1 year']['P_battery_ds']
temp_bess = pd.DataFrame(temp_bess_ch - temp_bess_ds)
temp_bess.columns = ['Battery Power Value']
del temp_bess_ch, temp_bess_ds

heatmap_bess_df = pd.DataFrame()
i = 0

while i < len(temp_bess):
    temp_df = temp_bess.iloc[i:i+96].reset_index(drop=True)
    temp_df.columns = [int(i/96)]
    
    heatmap_bess_df = pd.concat([heatmap_bess_df, temp_df], axis="columns")
    i = i + 96
heatmap_bess_df.index = heatmap_bess_df.index.map(lambda x: x*15/60)
heatmap_bess_df

0          1          2         3          4          5    \
0.00   52.999385  30.545100  25.549202  32.67485  30.545100  36.420507   
0.25   52.999385  30.545100  25.549202  32.67485  30.545100  35.820507   
0.50   52.999385  30.545100  25.549202  32.67485  30.545100  30.020507   
0.75   52.999385  30.545100  25.549202  32.67485  30.545100  28.420507   
1.00   52.999385  30.545100  25.549202  32.67485  30.545100  24.820507   
...          ...        ...        ...       ...        ...        ...   
22.75  30.545100  25.549202  32.674850  30.54510  36.420507   6.455140   
23.00  30.545100  25.549202  32.674850  30.54510  36.420507   6.455140   
23.25  30.545100  25.549202  32.674850  30.54510  36.420507   6.455140   
23.50  30.545100  25.549202  32.674850  30.54510  36.420507   6.455140   
23.75  30.545100  25.549202  32.674850  30.54510  36.420507   6.255140   

             6          7          8          9          10         11   \
0.00    6.255140  33.855121  31.574102  33.575977  34.022593  33.855121   
0.25    2.841014  33.855121  31.574102  33.575977  34.022593  33.855121   
0.50   -0.800000  33.855121  31.574102  33.575977  34.022593  33.855121   
0.75    0.000000  33.855121  31.574102  33.575977  34.022593  33.855121   
1.00    1.580772  33.855121  31.574102  33.575977  34.022593  33.855121   
...          ...        ...        ...        ...        ...        ...   
22.75  33.855121  31.574102  33.575977  34.022593  33.855121  26.250516   
23.00  33.855121  31.574102  33.575977  34.022593  33.855121  26.250516   
23.25  33.855121  31.574102  33.575977  34.022593  33.855121  31.986903   
23.50  33.855121  31.574102  33.575977  34.022593  33.855121  31.986903   
23.75  33.855121  31.574102  33.575977  34.022593  33.855121  31.986903   

             12        13         14         15         16         17   \
0.00   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
0.25   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
0.50   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
0.75   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
1.00   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
...          ...       ...        ...        ...        ...        ...   
22.75  30.545100  36.49138  34.140448  31.081878  33.855121  33.773315   
23.00  30.545100  36.49138  34.140448  31.081878  33.855121  33.773315   
23.25  30.545100  36.49138  34.140448  31.081878  33.855121  34.373315   
23.50  30.545100  36.49138  34.140448  31.081878  33.855121  34.973315   
23.75  30.545100  36.49138  34.140448  31.081878  33.855121  35.573315   

             18         19         20         21         22         23   \
0.00   35.573315  41.802036  32.524705  39.572874  35.209716  31.574102   
0.25   40.290449  41.802036  32.524705  39.572874  35.209716  31.574102   
0.50   40.290449  41.802036  32.524705  39.572874  35.209716  31.574102   
0.75   40.290449  41.802036  32.524705  39.572874  35.209716  31.574102   
1.00   40.290449  41.802036  32.524705  39.572874  35.209716  31.574102   
...          ...        ...        ...        ...        ...        ...   
22.75  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   
23.00  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   
23.25  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   
23.50  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   
23.75  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   

             24         25         26       27         28         29   \
0.00   37.969709  35.663142  32.773842  30.5451  30.545100  26.265182   
0.25   37.969709  35.663142  32.773842  30.5451  30.545100  26.265182   
0.50   37.969709  35.663142  32.773842  30.5451  30.545100  26.265182   
0.75   37.969709  35.663142  32.773842  30.5451  30.545100  26.265182   
1.00   37.969709  35.663142  32.773842  30.5451  30.545100  26.26518

In [48]:
pv_fig = px.imshow(heatmap_bess_df, color_continuous_scale='thermal', origin='lower', aspect='auto')
pv_fig.update_yaxes(tickformat=" ,~", nticks=24, range=[0, 24*4], dtick=1, ticks='outside',
                    tickvals=[i/4 for i in range(0, 96, 4)],
                    ticktext=[f'{int(i/4)}:00' for i in range(0, 96, 4)],
                    title=dict(font_size=22, text='<b>Hour in a day</b>'))

pv_fig.update_xaxes(griddash="dot", range=[0, 365], ticks='outside', title=dict(font_size=22, text='<b>Day in a year</b>'),
                    tickvals=[i for i in range(0, 365, 14)],
                    ticktext=[str(i+1) for i in range(0, 365, 14)])

plot_width = 950
plot_height = 550
pv_fig.update_layout(height=plot_height, width=plot_width, font_size=16,
                     coloraxis=dict(colorbar=dict(len=1.05, thickness=20, 
                                                  title=dict(text='<b>Battery Charging Power [kW]</b>', font_size=22,
                                                             side='right'))),
                     font_family="Computer Modern Roman")
# pv_fig.show()
if not os.path.exists(f"plots/{model}"):
    os.mkdir(f"plots/{model}")

pv_fig.write_image(f"plots/{model}/{model}_heatmap_battery_p_ch.png")

##### Prediction data - Battery max power

In [49]:
temp_bess = temp_data['optimised_variables']['15-min optimal data for 1 year'][['P_battery_max']].reset_index(drop=True)

heatmap_bess_df = pd.DataFrame()
i = 0

while i < len(temp_bess):
    temp_df = temp_bess.iloc[i:i+96].reset_index(drop=True)
    temp_df.columns = [int(i/96)]
    
    heatmap_bess_df = pd.concat([heatmap_bess_df, temp_df], axis="columns")
    i = i + 96
heatmap_bess_df.index = heatmap_bess_df.index.map(lambda x: x*15/60)
heatmap_bess_df

0          1          2         3          4          5    \
0.00   52.999385  30.545100  25.549202  32.67485  30.545100  36.420507   
0.25   52.999385  30.545100  25.549202  32.67485  30.545100  35.820507   
0.50   52.999385  30.545100  25.549202  32.67485  30.545100  30.020507   
0.75   52.999385  30.545100  25.549202  32.67485  30.545100  28.420507   
1.00   52.999385  30.545100  25.549202  32.67485  30.545100  24.820507   
...          ...        ...        ...       ...        ...        ...   
22.75  30.545100  25.549202  32.674850  30.54510  36.420507   6.455140   
23.00  30.545100  25.549202  32.674850  30.54510  36.420507   6.455140   
23.25  30.545100  25.549202  32.674850  30.54510  36.420507   6.455140   
23.50  30.545100  25.549202  32.674850  30.54510  36.420507   6.455140   
23.75  30.545100  25.549202  32.674850  30.54510  36.420507   6.255140   

             6          7          8          9          10         11   \
0.00    6.255140  33.855121  31.574102  33.575977  34.022593  33.855121   
0.25    2.841014  33.855121  31.574102  33.575977  34.022593  33.855121   
0.50    0.000000  33.855121  31.574102  33.575977  34.022593  33.855121   
0.75    0.000000  33.855121  31.574102  33.575977  34.022593  33.855121   
1.00    1.580772  33.855121  31.574102  33.575977  34.022593  33.855121   
...          ...        ...        ...        ...        ...        ...   
22.75  33.855121  31.574102  33.575977  34.022593  33.855121  26.250516   
23.00  33.855121  31.574102  33.575977  34.022593  33.855121  26.250516   
23.25  33.855121  31.574102  33.575977  34.022593  33.855121  31.986903   
23.50  33.855121  31.574102  33.575977  34.022593  33.855121  31.986903   
23.75  33.855121  31.574102  33.575977  34.022593  33.855121  31.986903   

             12        13         14         15         16         17   \
0.00   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
0.25   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
0.50   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
0.75   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
1.00   31.986903  30.54510  36.491380  34.140448  31.081878  33.855121   
...          ...       ...        ...        ...        ...        ...   
22.75  30.545100  36.49138  34.140448  31.081878  33.855121  33.773315   
23.00  30.545100  36.49138  34.140448  31.081878  33.855121  33.773315   
23.25  30.545100  36.49138  34.140448  31.081878  33.855121  34.373315   
23.50  30.545100  36.49138  34.140448  31.081878  33.855121  34.973315   
23.75  30.545100  36.49138  34.140448  31.081878  33.855121  35.573315   

             18         19         20         21         22         23   \
0.00   35.573315  41.802036  32.524705  39.572874  35.209716  31.574102   
0.25   40.290449  41.802036  32.524705  39.572874  35.209716  31.574102   
0.50   40.290449  41.802036  32.524705  39.572874  35.209716  31.574102   
0.75   40.290449  41.802036  32.524705  39.572874  35.209716  31.574102   
1.00   40.290449  41.802036  32.524705  39.572874  35.209716  31.574102   
...          ...        ...        ...        ...        ...        ...   
22.75  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   
23.00  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   
23.25  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   
23.50  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   
23.75  41.802036  32.524705  39.572874  35.209716  31.574102  37.969709   

             24         25         26       27         28         29   \
0.00   37.969709  35.663142  32.773842  30.5451  30.545100  26.265182   
0.25   37.969709  35.663142  32.773842  30.5451  30.545100  26.265182   
0.50   37.969709  35.663142  32.773842  30.5451  30.545100  26.265182   
0.75   37.969709  35.663142  32.773842  30.5451  30.545100  26.265182   
1.00   37.969709  35.663142  32.773842  30.5451  30.545100  26.26518

##### Prediction data - Grid power

In [50]:
temp_grid = temp_data['optimised_variables']['15-min optimal data for 1 year'][['P_grid']].reset_index(drop=True)

heatmap_grid_df = pd.DataFrame()
i = 0

while i < len(temp_grid):
    temp_df = temp_grid.iloc[i:i+96].reset_index(drop=True)
    temp_df.columns = [int(i/96)]
    
    heatmap_grid_df = pd.concat([heatmap_grid_df, temp_df], axis="columns")
    i = i + 96
heatmap_grid_df.index = heatmap_grid_df.index.map(lambda x: x*15/60)
heatmap_grid_df

0          1          2          3          4          5    \
0.00   65.799385  43.545100  49.621302  56.075859  47.510507  49.420507   
0.25   65.999385  43.345100  49.621302  55.875859  47.510507  74.420507   
0.50   65.799385  43.345100  42.172731  55.875859  47.510507  74.420507   
0.75   66.199385  43.545100  42.572731  55.875859  47.310507  74.420507   
1.00   66.399385  43.545100  41.972731  55.875859  47.110507  74.420507   
...          ...        ...        ...        ...        ...        ...   
22.75  46.089100  54.614030  55.875859  47.510507  50.020507  74.420507   
23.00  46.289100  54.814030  56.075859  47.510507  50.020507  74.420507   
23.25  46.289100  54.814030  55.875859  47.310507  49.620507  74.420507   
23.50  43.545100  54.614030  55.875859  47.310507  49.420507  74.420507   
23.75  43.545100  49.621302  55.875859  47.310507  49.820507  74.420507   

             6          7          8         9         10         11   \
0.00   74.420507  56.282752  50.374533  58.27480  61.96305  57.709460   
0.25   74.420507  56.282752  50.174533  58.27480  61.76305  57.709460   
0.50   74.420507  56.282752  50.374533  58.47480  61.96305  57.509460   
0.75   74.420507  56.482752  50.174533  58.47480  61.96305  53.929460   
1.00   74.420507  56.282752  50.374533  57.43480  61.76305  53.929460   
...          ...        ...        ...       ...       ...        ...   
22.75  60.082752  50.774533  58.674800  61.96305  61.50946  74.220507   
23.00  58.282752  50.574533  58.274800  61.76305  60.10946  74.420507   
23.25  58.682752  50.574533  58.274800  61.36305  61.30946  72.220507   
23.50  56.482752  50.574533  58.474800  61.56305  58.10946  74.420507   
23.75  55.882752  50.374533  58.074800  61.36305  57.70946  69.740162   

             12        13         14         15         16         17   \
0.00   68.140162  57.39020  59.146540  63.501167  52.541347  56.277474   
0.25   68.340162  57.59020  58.946540  48.740448  52.741347  56.277474   
0.50   68.140162  57.19020  58.946540  48.540448  52.541347  56.077474   
0.75   67.940162  57.39020  58.746540  48.540448  49.325347  56.077474   
1.00   67.940162  57.59020  58.746540  48.340448  49.125347  56.277474   
...          ...       ...        ...        ...        ...        ...   
22.75  57.190200  60.74654  66.487834  53.141347  59.677474  74.020507   
23.00  57.390200  60.74654  65.287834  52.941347  59.477474  74.420507   
23.25  56.990200  60.94654  64.887834  52.741347  57.877474  74.420507   
23.50  57.590200  58.94654  64.687834  52.541347  56.877474  74.420507   
23.75  57.390200  59.14654  64.287834  52.941347  56.677474  74.220507   

             18         19         20         21         22         23   \
0.00   74.420507  70.235553  48.924705  58.572874  65.602630  60.342505   
0.25   74.420507  68.235553  48.924705  58.172874  65.802630  60.142505   
0.50   74.420507  68.035553  48.924705  56.772874  57.956916  59.742505   
0.75   74.420507  67.835553  48.924705  56.572874  57.756916  59.742505   
1.00   74.420507  67.635553  48.524705  56.372874  58.156916  60.142505   
...          ...        ...        ...        ...        ...        ...   
22.75  71.420507  53.124705  63.372874  66.202630  61.542505  55.969709   
23.00  71.020507  52.324705  61.972874  66.002630  61.142505  55.969709   
23.25  70.420507  52.324705  61.572874  65.802630  60.742505  55.369709   
23.50  74.420507  49.524705  64.172874  65.802630  60.742505  54.169709   
23.75  69.835553  49.524705  61.172874  65.802630  60.142505  53.369709   

             24         25         26       27         28         29   \
0.00   53.369709  74.420507  62.700592  46.7451  45.345100  45.572231   
0.25   53.769709  74.420507  62.500592  45.5451  45.545100  45.372231   
0.50   53.569709  74.420507  62.300592  45.7451  45.545100  44.772231   
0.75   53.969709  74.420507  62.300592  45.5451  45.345100  43.678898   
1.00   53.569709  74.420507  54.211842  45.5451  45.345100  43.478898   
...    

In [51]:
pv_fig = px.imshow(heatmap_grid_df, color_continuous_scale='thermal', origin='lower', aspect='auto')
pv_fig.update_yaxes(tickformat=" ,~", nticks=24, range=[0, 24*4], dtick=1, ticks='outside',
                    tickvals=[i/4 for i in range(0, 96, 4)],
                    ticktext=[f'{int(i/4)}:00' for i in range(0, 96, 4)],
                    title=dict(font_size=22, text='<b>Hour in a day</b>'))

pv_fig.update_xaxes(griddash="dot", range=[0, 365], ticks='outside', title=dict(font_size=22, text='<b>Day in a year</b>'),
                    tickvals=[i for i in range(0, 365, 14)],
                    ticktext=[str(i+1) for i in range(0, 365, 14)])

plot_width = 950
plot_height = 550
pv_fig.update_layout(height=plot_height, width=plot_width, font_size=16,
                     coloraxis=dict(colorbar=dict(len=1.05, thickness=20, 
                                                  title=dict(text='<b>Grid Power [kW]</b>', font_size=22,
                                                             side='right'))),
                     font_family="Computer Modern Roman")
# pv_fig.show()
if not os.path.exists(f"plots/{model}"):
    os.mkdir(f"plots/{model}")

pv_fig.write_image(f"plots/{model}/{model}_heatmap_grid_p.png")

##### Prediction data - Grid positive power

##### Prediction data - Grid negative power

##### Prediction data - Grid electricity cost

##### Parameters

In [52]:
ov = temp_data['optimised_variables']['Optimal variables'][['P_pv_install', 'binary_pv', 'E_battery_capacity', 
                                                            'binary_battery', 'P_battery_MAX', 'P_contracted', 
                                                            'P_cs_contracted', 'C_total', 'C_invest', 'C_ee_operational', 
                                                            'C_ee_annual', 'C_profit_annual', 'C_profit', 'C_maintenance', 
                                                            'C_pv_maintenance', 'C_battery_maintenance', 'C_pl_maintenance', 
                                                            'C_loan', 'C_annuity', 'C_battery_replacement']]

In [53]:
ov.T

0
P_pv_install               60.000000
binary_pv                   1.000000
E_battery_capacity        247.330465
binary_battery              1.000000
P_battery_MAX              61.832616
P_contracted              150.000000
P_cs_contracted             0.000000
C_total                958387.579428
C_invest               103226.265136
C_ee_operational       848096.168980
C_ee_annual             59584.589516
C_profit_annual          5341.001713
C_profit                76021.050543
C_maintenance           35302.454281
C_pv_maintenance         1800.000000
C_battery_maintenance     989.321861
C_pl_maintenance          240.000000
C_loan                  40239.925557
C_annuity                5729.260111
C_battery_replacement    7543.816016

##### Prediction data - Grid Max Power Optimal Monthly Variables

In [54]:
temp_data['optimised_variables']['Optimal monthly variables'][['P_grid_max']].T

0          1          2          3          4          5   \
P_grid_max  74.420507  55.762344  59.293363  56.324608  44.699162  59.599242   

                   6          7          8          9         10         11  
P_grid_max  65.329013  40.779722  58.738701  57.530455  59.28893  60.402383

##### Prediction data

In [55]:
pv_predictions = pd.DataFrame(temp_data['optimised_variables']['15-min optimal data for 1 year'][['P_pv']])
pv_predictions.columns = ['PV']
pv_predictions['Day'] = pv_predictions.index // 96
pv_predictions

PV  Day
0      0.0    0
1      0.0    0
2      0.0    0
3      0.0    0
4      0.0    0
...    ...  ...
35035  0.0  364
35036  0.0  364
35037  0.0  364
35038  0.0  364
35039  0.0  364

[35040 rows x 2 columns]

In [56]:
pv_p = dict()
i = 0
max_day = pv_predictions['Day'].max() + 1
while i < max_day:
    pv_p[i] = pv_predictions.loc[pv_predictions['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [57]:
tdf = temp_data['optimised_variables']['15-min optimal data for 1 year']['P_battery_ch'] - temp_data['optimised_variables']['15-min optimal data for 1 year']['P_battery_ds']
bess_predictions = pd.DataFrame(tdf)
bess_predictions.columns = ['Battery Power Value']
# temp_b.replace(0, np.nan, inplace=True)
bess_predictions['Day'] = bess_predictions.index // 96

del tdf
bess_predictions

Battery Power Value  Day
0                52.999385    0
1                52.999385    0
2                52.999385    0
3                52.999385    0
4                52.999385    0
...                    ...  ...
35035             0.000000  364
35036             0.000000  364
35037             0.000000  364
35038             0.000000  364
35039             0.000000  364

[35040 rows x 2 columns]

In [58]:
bess_p = dict()
i = 0
max_day = bess_predictions['Day'].max() + 1
while i < max_day:
    bess_p[i] = bess_predictions.loc[bess_predictions['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [59]:
tdf = temp_data['optimised_variables']['15-min optimal data for 1 year']['E_battery'] / ov['E_battery_capacity'][0]
bess_soc_predict = pd.DataFrame(tdf)
bess_soc_predict.columns = ['Battery SOC']
# temp_b.replace(0, np.nan, inplace=True)
bess_soc_predict['Day'] = bess_soc_predict.index // 96

del tdf
bess_soc_predict

Battery SOC  Day
0         0.150893    0
1         0.201786    0
2         0.252679    0
3         0.303571    0
4         0.354464    0
...            ...  ...
35035     0.100000  364
35036     0.100000  364
35037     0.100000  364
35038     0.100000  364
35039     0.100000  364

[35040 rows x 2 columns]

In [60]:
bess_soc = dict()
i = 0
max_day = bess_soc_predict['Day'].max() + 1
while i < max_day:
    bess_soc[i] = bess_soc_predict.loc[bess_soc_predict['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [61]:
tdf = temp_data['optimised_variables']['15-min optimal data for 1 year']['P_battery_max']
bess_max_predict = pd.DataFrame(tdf)
bess_max_predict.columns = ['Battery MAX Power']
# temp_b.replace(0, np.nan, inplace=True)
bess_max_predict['Day'] = bess_max_predict.index // 96

del tdf
bess_max_predict

Battery MAX Power  Day
0              52.999385    0
1              52.999385    0
2              52.999385    0
3              52.999385    0
4              52.999385    0
...                  ...  ...
35035           0.000000  364
35036           0.000000  364
35037           0.000000  364
35038           0.000000  364
35039           0.000000  364

[35040 rows x 2 columns]

In [62]:
bess_max_p = dict()
i = 0
max_day = bess_max_predict['Day'].max() + 1
while i < max_day:
    bess_max_p[i] = bess_max_predict.loc[bess_max_predict['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [63]:
tdf = temp_data['optimised_variables']['15-min optimal data for 1 year']['P_battery_max_ch']
bess_max_ch_predict = pd.DataFrame(tdf)
bess_max_ch_predict.columns = ['Battery max charging Power']
# temp_b.replace(0, np.nan, inplace=True)
bess_max_ch_predict['Day'] = bess_max_ch_predict.index // 96

del tdf
bess_max_ch_predict

Battery max charging Power  Day
0                      525.025162    0
1                      493.556777    0
2                      462.088392    0
3                      430.620006    0
4                      399.151621    0
...                           ...  ...
35035                  556.493547  364
35036                  556.493547  364
35037                  556.493547  364
35038                  556.493547  364
35039                  556.493547  364

[35040 rows x 2 columns]

In [64]:
bess_max_ch_p = dict()
i = 0
max_day = bess_max_ch_predict['Day'].max() + 1
while i < max_day:
    bess_max_ch_p[i] = bess_max_ch_predict.loc[bess_max_ch_predict['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [65]:
bess_max_ch_power = bess_max_ch_predict.copy()
print(bess_max_ch_power)
bess_max_ch_power['Battery max charging Power'] = bess_max_ch_power.apply(lambda row: min(row['Battery max charging Power'], ov['P_battery_MAX'][0]), axis = 1)

       Battery max charging Power  Day
0                      525.025162    0
1                      493.556777    0
2                      462.088392    0
3                      430.620006    0
4                      399.151621    0
...                           ...  ...
35035                  556.493547  364
35036                  556.493547  364
35037                  556.493547  364
35038                  556.493547  364
35039                  556.493547  364

[35040 rows x 2 columns]


In [66]:
bess_max_ch_power

Battery max charging Power  Day
0                       61.832616    0
1                       61.832616    0
2                       61.832616    0
3                       61.832616    0
4                       61.832616    0
...                           ...  ...
35035                   61.832616  364
35036                   61.832616  364
35037                   61.832616  364
35038                   61.832616  364
35039                   61.832616  364

[35040 rows x 2 columns]

In [67]:
bess_max_ch = dict()
i = 0
max_day = bess_max_ch_power['Day'].max() + 1
while i < max_day:
    bess_max_ch[i] = bess_max_ch_power.loc[bess_max_ch_power['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [68]:
bess_max_power = bess_max_ch_predict.copy()
print(bess_max_power)
bess_max_power['Battery max charging Power'] = ov['P_battery_MAX'][0]

       Battery max charging Power  Day
0                      525.025162    0
1                      493.556777    0
2                      462.088392    0
3                      430.620006    0
4                      399.151621    0
...                           ...  ...
35035                  556.493547  364
35036                  556.493547  364
35037                  556.493547  364
35038                  556.493547  364
35039                  556.493547  364

[35040 rows x 2 columns]


In [69]:
b_max_power = dict()
i = 0
max_day = bess_max_power['Day'].max() + 1
while i < max_day:
    b_max_power[i] = bess_max_power.loc[bess_max_power['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [70]:
temp_data['optimised_variables']['15-min optimal data for 1 year']

Unnamed: 0  P_pv  E_battery  P_battery_ch  P_battery_ds  P_battery_max  \
0               0   0.0  37.320401     52.999385           0.0      52.999385   
1               1   0.0  49.907755     52.999385           0.0      52.999385   
2               2   0.0  62.495109     52.999385           0.0      52.999385   
3               3   0.0  75.082463     52.999385           0.0      52.999385   
4               4   0.0  87.669817     52.999385           0.0      52.999385   
...           ...   ...        ...           ...           ...            ...   
35035       35035   0.0  24.733047      0.000000           0.0       0.000000   
35036       35036   0.0  24.733047      0.000000           0.0       0.000000   
35037       35037   0.0  24.733047      0.000000           0.0       0.000000   
35038       35038   0.0  24.733047      0.000000           0.0       0.000000   
35039       35039   0.0  24.733047      0.000000           0.0       0.000000   

       P_battery_max_ch  Bat_ch_ramp     P_grid  P_grid_positive  \
0            525.025162          0.0  65.799385        65.799385   
1            493.556777          0.0  65.999385        65.999385   
2            462.088392          0.0  65.799385        65.799385   
3            430.620006          0.0  66.199385        66.199385   
4            399.151621          0.0  66.399385        66.399385   
...                 ...          ...        ...              ...   
35035        556.493547          0.0  14.800000        14.800000   
35036        556.493547          0.0  14.800000        14.800000   
35037        556.493547          0.0  14.600000        14.600000   
35038        556.493547          0.0  14.200000        14.200000   
35039        556.493547          0.0  13.800000        13.800000   

       P_grid_negative  C_ee_hourly  C_profit_hourly  
0                  0.0     3.214662              0.0  
1                  0.0     3.224433              0.0  
2                  0.0     3.214662              0.0  
3                  0.0     3.234204              0.0  
4                  0.0     3.243975              0.0  
...                ...          ...              ...  
35035              0.0     0.723061              0.0  
35036              0.0     0.723061              0.0  
35037              0.0     0.713290              0.0  
35038              0.0     0.693748              0.0  
35039              0.0     0.674206              0.0  

[35040 rows x 13 columns]

In [71]:
tdf = temp_data['optimised_variables']['15-min optimal data for 1 year']['P_grid_positive'] - temp_data['optimised_variables']['15-min optimal data for 1 year']['P_grid_negative']
grid_predict = pd.DataFrame(tdf)
grid_predict.columns = ['Grid Power Value']
# temp_b.replace(0, np.nan, inplace=True)
grid_predict['Day'] = grid_predict.index // 96

del tdf
grid_predict

Grid Power Value  Day
0             65.799385    0
1             65.999385    0
2             65.799385    0
3             66.199385    0
4             66.399385    0
...                 ...  ...
35035         14.800000  364
35036         14.800000  364
35037         14.600000  364
35038         14.200000  364
35039         13.800000  364

[35040 rows x 2 columns]

In [72]:
grid_predict.loc[grid_predict['Grid Power Value'] == grid_predict['Grid Power Value'].max(), :]

Grid Power Value  Day
27           74.420507    0
313          74.420507    3
314          74.420507    3
315          74.420507    3
374          74.420507    3
...                ...  ...
2495         74.420507   25
2715         74.420507   28
2772         74.420507   28
2811         74.420507   29
2907         74.420507   30

[310 rows x 2 columns]

In [73]:
grid_p = dict()
i = 0
max_day = grid_predict['Day'].max() + 1
while i < max_day:
    grid_p[i] = grid_predict.loc[grid_predict['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [74]:
tdf = temp_data['optimised_variables']['15-min optimal data for 1 year']['C_ee_hourly'] - temp_data['optimised_variables']['15-min optimal data for 1 year']['C_profit_hourly']
cost_predictions = pd.DataFrame(tdf)
cost_predictions.columns = ['Cost/Profit']
# temp_b.replace(0, np.nan, inplace=True)
cost_predictions['Day'] = cost_predictions.index // 96

del tdf
cost_predictions

Cost/Profit  Day
0         3.214662    0
1         3.224433    0
2         3.214662    0
3         3.234204    0
4         3.243975    0
...            ...  ...
35035     0.723061  364
35036     0.723061  364
35037     0.713290  364
35038     0.693748  364
35039     0.674206  364

[35040 rows x 2 columns]

In [75]:
cost = dict()
i = 0
max_day = cost_predictions['Day'].max() + 1
while i < max_day:
    cost[i] = cost_predictions.loc[cost_predictions['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [76]:
def plot_single_day_battery_predictions(day, model=''):
    day_length = len(bess_soc[day])

    subplot_fig = make_subplots(
        rows=1,
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.04,
        specs=[[{'secondary_y': True}]]
    )

    subplot_fig.add_scatter(y=bess_soc[day]['Battery SOC'], yaxis='y', row=1, col=1, secondary_y=False, legendgroup='bsoc',
                            x=bess_soc[day].index, line_shape='linear', name='State of Charge %', mode='markers+lines',
                            marker=dict(size=5, symbol='circle-dot'), line=dict(color='orange'), showlegend=True)

    subplot_fig.add_bar(y=bess_soc[day]['Battery SOC'], showlegend=False, yaxis='y2', width=0.9, row=1, col=1, 
                        secondary_y=False,
                        marker=dict(color='darkorange', coloraxis='coloraxis', opacity=0.3, line_width=0), name='soc', 
                        legendgroup='bsoc')

#     subplot_fig.add_bar(y=bess_max_p[day]['Battery MAX Power'], showlegend=True, yaxis='y3', width=0.9, row=1, col=1, 
#                         secondary_y=True, legendgroup='max power',
#                         marker=dict(color='crimson', pattern=dict(shape='\\', fillmode='replace', size=5), opacity=0.85, 
#                                     line_width=1.2, line_color='red'), name='Battery max charging Power [kW]')
    subplot_fig.add_bar(y=bess_p[day]['Battery Power Value'], showlegend=True, yaxis='y3', width=0.9, row=1, col=1, 
                        secondary_y=True, legendgroup='power',
                        marker=dict(color='dimgrey', pattern=dict(shape='/', fillmode='replace', size=15), opacity=0.8, 
                                    line_width=1.2, line_color='dimgrey'), name='Battery Power [kW]')
    
    subplot_fig.add_scatter(y=-b_max_power[day]['Battery max charging Power'], line_shape='linear', secondary_y=True, 
                            name='Battery Max Discharging Power [kW]', mode='markers+lines', yaxis='y3', row=1, col=1, 
                            legendgroup='max power',
                            marker=dict(size=0, symbol='cross', opacity=0), line=dict(color='crimson'), 
                            showlegend=True)
    subplot_fig.add_scatter(y=bess_p[day]['Battery Power Value'], line_shape='linear', secondary_y=True,
                            name='Battery Power [kW]', mode='markers', yaxis='y3', row=1, col=1, legendgroup='power',
                            marker=dict(size=5, symbol='circle', opacity=0.7), line=dict(color='black'), showlegend=False)
    
    subplot_fig.add_scatter(y=bess_max_ch[day]['Battery max charging Power'], line_shape='linear', secondary_y=True,
                            name='Battery Max Charging Power [kW]', mode='markers+lines', yaxis='y3', row=1, col=1, 
                            legendgroup='power',
                            marker=dict(size=0, symbol='cross', opacity=0), line=dict(color='darkturquoise'), showlegend=True)
#     subplot_fig.add_scatter(y=bess_max_ch_p[day]['Battery max charging Power'], line_shape='linear', secondary_y=True,
#                             name='Battery max charging Power [kW]', mode='markers', yaxis='y3', row=1, col=1, 
# legendgroup='power',
#                             marker=dict(size=5, symbol='circle', opacity=0.7), line=dict(color='green'),showlegend=False)
#     subplot_fig.add_scatter(y=-b_max_power[day]['Battery max charging Power'], line_shape='linear', secondary_y=True,
#                             name='Battery MAX Power [kW]', mode='markers', yaxis='y3', row=1, col=1, legendgroup='power',
#                             marker=dict(size=5, symbol='circle', opacity=0.7), line=dict(color='green'), showlegend=False)

    subplot_fig.add_annotation(x=12/26, y=-0.1, text="<b>Timestep in a Day (h)</b>", textangle=0, xref="paper", 
                               yref="paper", font_size=22, showarrow=False)

    max_timestep = max(day_length, 100)
    # Predicted Battery Values
    subplot_fig.update_layout(title="",
                              yaxis=dict(title=''), barmode='overlay')
    subplot_fig.update_xaxes(tickformat='', griddash="dot", range=[-0.4, day_length+0.4],
                             tickvals=[i for i in range(0, max_timestep, 4)], tickfont=dict(size=20),
                             ticktext=[str(int(i/4)%24) for i in range(0, max_timestep, 4)])

    # For plot export: w(1280)xh(720), w(1920)xh(1080)
    # For better overview in jupyter: w(850)xh(650)
    plot_width = 1050
    plot_height = 690
    
    if model == 'model1':
        max_power_ratio = 0.68
    elif model == 'model2':
        max_power_ratio = 0.65
    else:
        max_power_ratio = 0.70
    
    if model == 'model2':
        legend_x = 11.5/24
        legend_y = 0.97
    else:
        legend_x = 0.2/24
        legend_y = 0.07
    
    max_power = ((ov['P_battery_MAX'][0]//10)*10 + 10)*1.5
    subplot_fig.update_layout(height=plot_height, width=plot_width, title=dict(xanchor="center", x=12/32, 
                                                                               font_size=24, y=0.92), 
                              showlegend=True, font_family="Computer Modern Roman", 
                              legend=dict(x=legend_x, y=legend_y, bgcolor='rgba(255,255,255,0.2)', font_size=22,
                                          groupclick='togglegroup'),
                              yaxis=dict(tickformat=" ,~%", nticks=5, range=[-0.79, 1.1], dtick=0.25, tickfont=dict(size=22),
                                         title=dict(text='<b>State of Charge</b>', font_size=24)),
                              yaxis2=dict(tickformat=" ,~", dtick=max_power//7, nticks=5, tickfont=dict(size=22),
                                          range=[-max_power*max_power_ratio-1, max_power], title=dict(text='<b>Power [kW]</b>', font_size=22)),
                              yaxis3=dict(tickformat=" ,~g", tickfont=dict(size=22), nticks=6, title=dict(text=f'', font_size=22)))

#     subplot_fig.show()
    if not os.path.exists(f"plots/{model}"):
        os.mkdir(f"plots/{model}")

    subplot_fig.write_image(f"plots/{model}/{model}_battery_day_{day}.png")

    del plot_width, plot_height

In [77]:
def plot_days_range_battery_predictions(first_day=0, last_day=0, model=''):
    for d in range(first_day, last_day + 1, 1):
        plot_single_day_battery_predictions(day=d, model=model)
    print('------------------------------------\n'
          'Finished plotting days predicted battery stats.\n'
          '------------------------------------\n')

In [78]:
def plot_single_day_grid_cost_predictions(day, model=''):
    day_length = len(cost[day])
    t = day_length/24
    
    subplot_fig = go.Figure()

    total_cost = cost[day]['Cost/Profit']
    
    if day > 84 and day < 302:
        high_tariff_start = 8*t
        high_tariff_end = 22*t
    else:
        high_tariff_start = 7*t
        high_tariff_end = 21*t

    subplot_fig.add_vrect(x0=0, x1=high_tariff_start, fillcolor='grey', opacity=0.1, layer='above', line=dict(width=0))
    subplot_fig.add_annotation(x=3.5/24, y=1.05, text="Low Tariff", xanchor='center', yanchor='middle', xref="paper", 
                               yref="paper", font=dict(size=22, color='dimgrey'), showarrow=False)
    subplot_fig.add_vrect(x0=high_tariff_start, x1=high_tariff_end, fillcolor='gold', opacity=0.1, layer='above', 
                          line=dict(width=0))
    subplot_fig.add_annotation(x=13.5/24, y=1.05, text="Peak Tariff", xanchor='center', yanchor='middle', xref="paper", 
                               yref="paper", font=dict(size=22, color='goldenrod'), showarrow=False)
    subplot_fig.add_vrect(x0=high_tariff_end, x1=day_length, fillcolor='grey', opacity=0.1, layer='above', 
                          line=dict(width=0))
    subplot_fig.add_annotation(x=22.5/24, y=1.05, text="Low Tariff", xanchor='center', yanchor='middle', xref="paper", 
                               yref="paper", font=dict(size=22, color='dimgrey'), showarrow=False)

    subplot_fig.add_bar(y=total_cost, showlegend=False, yaxis='y', width=0.9, legendgroup='Grid Energy Cost',
                        marker=dict(color='silver', opacity=0.9, line_width=0), name='Grid Energy Cost')

    subplot_fig.add_scatter(x=cost[day].index, y=total_cost, line_shape='linear', name='(+)Cost/Profit(-)', mode='markers',
                            marker=dict(size=5, symbol='diamond', line=dict(width=1.5), color='black'), 
                            line=dict(color='rgba(0,0,0,0.7)'),
                            showlegend=False, yaxis='y', legendgroup='Grid Energy Cost')

    subplot_fig.add_annotation(x=-0.07, y=0.5, text="<b>Cost/Profit Value [€]</b>", xanchor='left', yanchor='middle', 
                               textangle=-90, xref="paper", yref="paper", font_size=24, showarrow=False)
    subplot_fig.add_annotation(x=0.5, y=-0.12, text="<b>Timestep (Hour) in a Day</b>", textangle=0, xref="paper", 
                               yref="paper", font_size=22, showarrow=False)

    max_timestep = max(day_length, 100)

    subplot_fig.update_layout(title="",
                              yaxis=dict(title=''), barmode='overlay')
    subplot_fig.update_xaxes(tickformat='', griddash="dot", title='', range=[-0.4, day_length+0.4],
                             tickvals=[i for i in range(0, max_timestep, 4)], tickfont=dict(size=20),
                             ticktext=[str(int(i/4)%24) for i in range(0, max_timestep, 4)])

    # For plot export: w(1280)xh(720), w(1920)xh(1080)
    # For better overview in jupyter: w(850)xh(650)
    plot_width = 980
    plot_height = 650


    total_cost_max = total_cost.max()
    subplot_fig.update_yaxes(nticks=6)
    subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman",
                              title=dict(xanchor="center", x=0.5, font_size=24, y=0.99), 
                              showlegend=True, 
                              coloraxis=dict(colorscale=[[0, 'rgb(22, 22, 22)'], [0.25, 'dimgrey'], 
                                                         [0.5, 'lightgrey'], [0.7, '#E93556'], [0.9, 'crimson'], 
                                                         [1, '#B81432']], 
                                             colorbar=dict(title=dict(text='<b>Cost/Profit Value [€]</b>', side='right'), 
                                                           thickness=15)), barmode='stack',
                              legend=dict(x=0.5, orientation='h', yanchor='bottom',
                                          entrywidth=0, y=1.01, xanchor='center'), scattermode='overlay',
                              yaxis=dict(tickformat=" ,.2~g", tickfont=dict(size=20)))


#     subplot_fig.show()
    if not os.path.exists(f"plots/{model}"):
        os.mkdir(f"plots/{model}")

    subplot_fig.write_image(f"plots/{model}/{model}_cost_day_{day}.png")

    del max_timestep, plot_width, plot_height

In [79]:
def plot_days_range_grid_cost_predictions(first_day=0, last_day=0, model=''):
    for d in range(first_day, last_day + 1, 1):
        plot_single_day_grid_cost_predictions(day=d, model=model)
    print('------------------------------------\n'
          'Finished plotting days predicted grid cost.\n'
          '------------------------------------\n')

##### Prediction data - powers

In [80]:
grid_p[0]

Grid Power Value  Day
0          65.799385    0
1          65.999385    0
2          65.799385    0
3          66.199385    0
4          66.399385    0
..               ...  ...
91         46.089100    0
92         46.289100    0
93         46.289100    0
94         43.545100    0
95         43.545100    0

[96 rows x 2 columns]

In [81]:
if 'Lot1' in temp_data['charging_schedule']['P_ev_ch'].columns:
    total_ch_p = pd.DataFrame({'Total Power': [0]*len(temp_data['charging_schedule']['P_ev_ch'].index),
                               'Total Charging Power': [0]*len(temp_data['charging_schedule']['P_ev_ch'].index),
                               'Total Discharging Power': [0]*len(temp_data['charging_schedule']['P_ev_ds'].index)})

    for charger in chargers:
        total_ch_p['Total Power'] = total_ch_p['Total Power'] + temp_data['charging_schedule']['P_ev_ch'][charger]
        total_ch_p['Total Charging Power'] = total_ch_p['Total Charging Power'] + temp_data['charging_schedule']['P_ev_ch'][charger]
        total_ch_p['Total Discharging Power'] = total_ch_p['Total Discharging Power'] + temp_data['charging_schedule']['P_ev_ds'][charger]
        if model == 'model2' or model == 'model4':
            total_ch_p['Total Power'] = total_ch_p['Total Power'] - temp_data['charging_schedule']['P_ev_ds'][charger]
    
    total_ch_p['Day'] = total_ch_p.index // 96
total_ch_p

Total Power  Total Charging Power  Total Discharging Power  Day
0              0.0                   0.0                      0.0    0
1              0.0                   0.0                      0.0    0
2              0.0                   0.0                      0.0    0
3              0.0                   0.0                      0.0    0
4              0.0                   0.0                      0.0    0
...            ...                   ...                      ...  ...
35035          0.0                   0.0                      0.0  364
35036          0.0                   0.0                      0.0  364
35037          0.0                   0.0                      0.0  364
35038          0.0                   0.0                      0.0  364
35039          0.0                   0.0                      0.0  364

[35040 rows x 4 columns]

In [82]:
temp_total_ev_p = total_ch_p[['Total Power']]

heatmap_ev_df = pd.DataFrame()
i = 0

while i < len(temp_total_ev_p):
    temp_df = temp_total_ev_p.iloc[i:i+96].reset_index(drop=True)
    temp_df.columns = [int(i/96)]
    
    heatmap_ev_df = pd.concat([heatmap_ev_df, temp_df], axis="columns")
    i = i + 96
heatmap_ev_df.index = heatmap_ev_df.index.map(lambda x: x*15/60)
heatmap_ev_df

0          1          2         3         4          5          6    \
0.00   0.000   0.000000  11.072101  9.601009  3.765407   0.000000  13.565367   
0.25   0.000   0.000000  11.072101  9.601009  3.765407   0.000000   0.179493   
0.50   0.000   0.000000   3.623529  9.601009  3.765407   0.000000  -0.179493   
0.75   0.000   0.000000   3.623529  9.601009  3.765407   0.000000  -0.179493   
1.00   0.000   0.000000   3.623529  9.601009  3.765407   0.000000   1.239735   
...      ...        ...        ...       ...       ...        ...        ...   
22.75  2.544  16.264828   9.601009  3.765407  0.000000   9.365367   7.027631   
23.00  2.544  16.264828   9.601009  3.765407  0.000000   9.365367   7.027631   
23.25  2.544  16.264828   9.601009  3.765407  0.000000  10.165367   7.027631   
23.50  0.000  16.264828   9.601009  3.765407  0.000000  13.165367   7.027631   
23.75  0.000  11.072101   9.601009  3.765407  0.000000  13.165367   7.027631   

            7          8          9          10         11         12   \
0.00   7.027631   4.800431  10.898824  13.740456   9.054339  22.553259   
0.25   7.027631   4.800431  10.898824  13.740456   9.054339  22.553259   
0.50   7.027631   4.800431  10.898824  13.740456   9.054339  22.553259   
0.75   7.027631   4.800431  10.898824  13.740456   5.474339  22.553259   
1.00   7.027631   4.800431  10.058824  13.740456   5.474339  22.553259   
...         ...        ...        ...        ...        ...        ...   
22.75  4.800431  10.898824  13.740456   9.054339  30.169991  11.645099   
23.00  4.800431  10.898824  13.740456   9.054339  30.169991  11.645099   
23.25  4.800431  10.898824  13.740456   9.054339  23.433604  11.645099   
23.50  4.800431  10.898824  13.740456   9.054339  23.433604  11.645099   
23.75  4.800431  10.898824  13.740456   9.054339  22.553259  11.645099   

             13         14         15        16         17         18   \
0.00   11.645099   8.255159  14.760719  6.059469   7.422353  22.047191   
0.25   11.645099   8.255159   0.000000  6.059469   7.422353  17.330058   
0.50   11.645099   8.255159   0.000000  6.059469   7.422353  17.530058   
0.75   11.645099   8.255159   0.000000  2.643469   7.422353  17.730058   
1.00   11.645099   8.255159   0.000000  2.643469   7.422353  18.130058   
...          ...        ...        ...       ...        ...        ...   
22.75   8.255159  15.347385   6.059469  7.422353  22.047191   7.218471   
23.00   8.255159  15.347385   6.059469  7.422353  22.047191   7.218471   
23.25   8.255159  15.347385   6.059469  7.422353  22.047191   7.218471   
23.50   8.255159  15.347385   6.059469  7.422353  22.047191   7.218471   
23.75   8.255159  15.347385   6.059469  7.422353  22.047191   9.633517   

            19   20         21         22         23         24         25   \
0.00   9.633517  0.0   0.000000  15.192914  13.368403   0.000000  20.757365   
0.25   9.633517  0.0   0.000000  15.192914  13.368403   0.000000  21.357365   
0.50   9.633517  0.0   0.000000   8.147200  13.368403   0.000000  22.357365   
0.75   9.633517  0.0   0.000000   8.147200  13.368403   0.000000  22.757365   
1.00   9.633517  0.0   0.000000   8.147200  13.368403   0.000000  22.757365   
...         ...  ...        ...        ...        ...        ...        ...   
22.75  0.000000  0.0  15.192914  13.368403   0.000000   8.673574  26.576750   
23.00  0.000000  0.0  15.192914  13.368403   0.000000   9.673574  26.576750   
23.25  0.000000  0.0  15.192914  13.368403   0.000000   9.673574  26.576750   
23.50  0.000000  0.0  15.192914  13.368403   0.000000  14.357365  26.576750   
23.75  0.000000  0.0  15.192914  13.368403   0.000000  20.357365  26.576750   

            26   27        28        29        30        31         32   \
0.00   13.92675  0.0  0.000000  4.907049  6.620432  7.326021   6.466316   
0.25   13.92675  0.0  0.000000  4.907049  6.620432  7.326021   6.466316   
0.50   13.92675  0.0  0.000000  4.907049  6.620432  7.326021   6.466316   
0.75   13.92675  0.0 

In [83]:
ev_fig = px.imshow(heatmap_ev_df, color_continuous_scale='thermal', origin='lower', aspect='auto')
ev_fig.update_yaxes(tickformat=" ,~", nticks=24, range=[0, 24*4], dtick=1, ticks='outside',
                    tickvals=[i/4 for i in range(0, 96, 4)],
                    ticktext=[f'{int(i/4)}:00' for i in range(0, 96, 4)],
                    title=dict(font_size=22, text='<b>Hour in a day</b>'))

ev_fig.update_xaxes(griddash="dot", range=[0, 365], ticks='outside',
                    title=dict(font_size=22, text='<b>Day in a year</b>'),
                    tickvals=[i for i in range(0, 365, 14)],
                    ticktext=[str(i+1) for i in range(0, 365, 14)])

plot_width = 950
plot_height = 550
ev_fig.update_layout(height=plot_height, width=plot_width, font_size=16,
                     coloraxis=dict(colorbar=dict(len=1.05, thickness=20, 
                                                  title=dict(text='<b>Total EV Dis/Charging Power [kW]</b>',
                                                             font_size=22,
                                                             side='right'))),
                     font_family="Computer Modern Roman")
# ev_fig.show()
if not os.path.exists(f"plots/{model}"):
    os.mkdir(f"plots/{model}")

ev_fig.write_image(f"plots/{model}/{model}_heatmap_ev_p_chds.png")
ev_fig.show()

In [84]:
total_ch_p.loc[total_ch_p['Total Power'] == total_ch_p['Total Power'].max(), :]

Total Power  Total Charging Power  Total Discharging Power  Day
8863    64.129086             64.230295                 0.101209   92

In [85]:
total_vehicle_power_predictions = dict()
i = 0
max_day = total_ch_p['Day'].max() + 1
while i < max_day:
    total_vehicle_power_predictions[i] = total_ch_p.loc[total_ch_p['Day'] == i, :].reset_index(drop=True)
    i = i + 1

In [86]:
ov

P_pv_install  binary_pv  E_battery_capacity  binary_battery  P_battery_MAX  \
0          60.0          1          247.330465               1      61.832616   

   P_contracted  P_cs_contracted        C_total       C_invest  \
0           150                0  958387.579428  103226.265136   

   C_ee_operational   C_ee_annual  C_profit_annual      C_profit  \
0      848096.16898  59584.589516      5341.001713  76021.050543   

   C_maintenance  C_pv_maintenance  C_battery_maintenance  C_pl_maintenance  \
0   35302.454281              1800             989.321861               240   

         C_loan    C_annuity  C_battery_replacement  
0  40239.925557  5729.260111            7543.816016

In [87]:
def plot_single_day_all_power_predictions(day, model=''):
    day_length = len(cost[day])
    t = day_length/24
    
    subplot_fig = go.Figure()

    grid_power = grid_p[day]['Grid Power Value']
    pv_power = pv_p[day]['PV']
    total_ev_p = total_vehicle_power_predictions[day]['Total Power']
    total_ev_p_ch = total_vehicle_power_predictions[day]['Total Charging Power']
    total_ev_p_ds = total_vehicle_power_predictions[day]['Total Discharging Power']
    battery_p = bess_p[day]['Battery Power Value']
#     battery_max_p = bess_max_p[day]['Battery MAX Power']
    battery_soc = bess_soc[day]['Battery SOC']
    # day_tariff = costs_predictions['Electricity Day Tariffs']
    
#     if model == 'model3' or model == 'model4':
    building_od = building_demand[day]['Building Demand']
    contracted_demand = temp_data['parameters'].T['BO_P_contracted_OD']['VALUE']
    
    if day > 84 and day < 302:
        high_tariff_start = 8*t
        high_tariff_end = 22*t
    else:
        high_tariff_start = 7*t
        high_tariff_end = 21*t

    subplot_fig.add_vrect(x0=0, x1=high_tariff_start, fillcolor='grey', opacity=0.1, layer='above', line=dict(width=0))
    subplot_fig.add_annotation(x=3.5/24, y=0.03, text="Low Tariff", xanchor='center', yanchor='middle', xref="paper", 
                               yref="paper", font=dict(size=22, color='dimgrey'), showarrow=False)
    subplot_fig.add_vrect(x0=high_tariff_start, x1=high_tariff_end, fillcolor='gold', opacity=0.1, layer='above', 
                          line=dict(width=0))
    subplot_fig.add_annotation(x=13.5/24, y=0.03, text="Peak Tariff", xanchor='center', yanchor='middle', xref="paper", 
                               yref="paper", font=dict(size=22, color='goldenrod'), showarrow=False)
    subplot_fig.add_vrect(x0=high_tariff_end, x1=day_length, fillcolor='grey', opacity=0.1, layer='above', 
                          line=dict(width=0))
    subplot_fig.add_annotation(x=22/24, y=0.03, text="Low Tariff", xanchor='center', yanchor='middle', xref="paper", 
                               yref="paper", font=dict(size=22, color='dimgrey'), showarrow=False)
    
    subplot_fig.add_hline(y=ov['P_contracted'][0], line_width=1.5, line_color="darkturquoise", opacity=0.5,
                          line_dash="dot", annotation_text="<i>Nanogrid Contracted Power</i>",
                          annotation_position="top left", annotation_font_size=22, 
                          annotation_font_color="darkturquoise",
                          annotation_opacity=0.5)
    subplot_fig.add_hline(y=-ov['P_contracted'][0], line_width=1.5, line_color="darkturquoise", opacity=0.5,
                          line_dash="dot", annotation_text="<i>-Nanogrid Contracted Power</i>",
                          annotation_position="top left", annotation_font_size=22, 
                          annotation_font_color="darkturquoise",
                          annotation_opacity=0.5)
    subplot_fig.add_hline(y=contracted_demand, line_width=1.5, line_color="sienna", opacity=0.5,
                          line_dash="dot", annotation_text="<i>Contracted Building Power Demand</i>", 
                          annotation_position="top left", annotation_font_size=22, annotation_font_color="dimgrey",
                          annotation_opacity=0.5)

    subplot_fig.add_scatter(x=cost[day].index, y=grid_power, line_shape='linear', name='Grid Power', mode='lines',
                            marker=dict(size=0, symbol='circle', line=dict(width=0), color='turquoise', 
                                        coloraxis='coloraxis'), line=dict(color='turquoise'),
                            showlegend=True, yaxis='y', legendgroup='Grid Power')
    subplot_fig.add_scatter(x=cost[day].index, y=pv_power, line_shape='linear', name='Solar Power', mode='lines',
                            marker=dict(size=0, symbol='circle', line=dict(width=0), color='gold', 
                                        coloraxis='coloraxis'), line=dict(color='gold'),
                            showlegend=True, yaxis='y2', legendgroup='Solar Power')
#     subplot_fig.add_scatter(x=cost[day].index, y=total_ev_p, line_shape='linear', name='Total Vehicle Power', 
#                             mode='lines',
#                             marker=dict(size=0, symbol='circle', line=dict(width=0), color='limegreen', 
#                                         coloraxis='coloraxis'), line=dict(color='limegreen'),
#                             showlegend=True, yaxis='y2', legendgroup='Total Power')
    subplot_fig.add_scatter(x=cost[day].index, y=total_ev_p_ch, line_shape='linear', name='Total Vehicle Charging Power', 
                            mode='lines',
                            marker=dict(size=0, symbol='circle', line=dict(width=0), color='limegreen', 
                                        coloraxis='coloraxis'), line=dict(color='limegreen'),
                            showlegend=True, yaxis='y2', legendgroup='Total EV Charging Power')
    if model == 'model1' or model == 'model3':
        show = False
    else:
        show = True
    subplot_fig.add_scatter(x=cost[day].index, y=-total_ev_p_ds, line_shape='linear', name='Total Vehicle Discharging Power', 
                            mode='lines',
                            marker=dict(size=0, symbol='circle', line=dict(width=0), color='limegreen', 
                                        coloraxis='coloraxis'), line=dict(color='limegreen', dash='dot'),
                            showlegend=show, yaxis='y2', legendgroup='Total EV Discharging Power')
    subplot_fig.add_scatter(x=cost[day].index, y=battery_p, line_shape='linear', name='Battery Power', mode='lines',
                            marker=dict(size=0, symbol='circle', line=dict(width=0), color='crimson', 
                                        coloraxis='coloraxis'), line=dict(color='crimson'),
                            showlegend=True, yaxis='y2', legendgroup='BESS Power')
    
    subplot_fig.add_scatter(x=cost[day].index, y=building_od, line_shape='linear', name='Building Power Demand', 
                            mode='lines',
                            marker=dict(size=0, symbol='circle', line=dict(width=0), color='dimgrey', 
                                        coloraxis='coloraxis'), line=dict(color='dimgrey'),
                            showlegend=True, yaxis='y', legendgroup='Building Power Demand')
#     subplot_fig.add_scatter(x=cost[day].index, y=battery_max_p, line_shape='linear', name='Battery Max Power', 
# mode='lines+markers',
#                             marker=dict(size=0, symbol='circle', line=dict(width=0), color='indianred', 
# coloraxis='coloraxis'), line=dict(color='indianred'),
#                             showlegend=True, yaxis='y', legendgroup='BESS Max Power')
#     subplot_fig.add_scatter(x=cost[day].index, y=battery_soc, line_shape='linear', name='Battery SOC', 
# mode='lines+markers',
#                             marker=dict(size=4, symbol='square', line=dict(width=0), color='dimgrey', 
# coloraxis='coloraxis'), line=dict(color='dimgrey'),
#                             showlegend=True, yaxis='y2', legendgroup='SOC')
    # # Electricity Day Tariff
    # subplot_fig.add_scatter(x=costs_predictions.index, y=day_tariff, line_shape='hv', 
#     name='Dnevna tarifa električne energije', mode='lines+markers',
    #                         marker=dict(size=0, symbol='circle', line=dict(width=0), color='teal', 
#     coloraxis='coloraxis'), line=dict(color='teal'),
    #                         showlegend=True, yaxis='y2', legendgroup='Day Tariff')

#     if model == 'model3' or model == 'model4':
    y_text = '<b>Grid & Building Power [kW]</b>'
#     else:
#         y_text = '<b>Grid Power [kW]</b>'
    subplot_fig.add_annotation(x=-0.08, y=0.5, text=y_text, xanchor='left', yanchor='middle', textangle=-90, 
                               xref="paper", yref="paper", font_size=24, showarrow=False)
    subplot_fig.add_annotation(x=1.04, y=0.5, text="<b>PV, Total Vehicle & Battery Power [kW]</b>", xanchor='left', 
                               yanchor='middle', textangle=-90, xref="paper", yref="paper", font_size=24, showarrow=False)
    subplot_fig.add_annotation(x=0.5, y=-0.1, text="<b>Timestep (Hour) in a Day</b>", textangle=0, xref="paper", 
                               yref="paper", font_size=24, showarrow=False)

    subplot_fig.add_shape(type="line", line_width=1.5, xref="paper", yref="y2", x0=0, y0=bess_max_ch[day]['Battery max charging Power'].iloc[0], 
                          label=dict(text="<i>MAX Battery Power</i>", textposition='end', font=dict(color='crimson', 
                                                                                                    size=22)),
                          x1=1, y1=bess_max_ch[day]['Battery max charging Power'].iloc[0], line=dict(color="crimson", dash="dot"), opacity=0.5)
    
    subplot_fig.add_shape(type="line", line_width=1.5, xref="paper", yref="y2", x0=0, y0=-b_max_power[day]['Battery max charging Power'].iloc[0], 
                          label=dict(text="<i>-MAX Battery Power</i>", textposition='end', font=dict(color='crimson', 
                                                                                                     size=22)),
                          x1=1, y1=-b_max_power[day]['Battery max charging Power'].iloc[0], line=dict(color="crimson", dash="dot"), opacity=0.5)
    
    subplot_fig.add_shape(type="rect", xref="paper", yref="y2", x0=0, y0=ov['P_pv_install'][0],
                          label=dict(text="<i>PV System Installed Power</i>", textposition='bottom left', 
                                     font=dict(color='darkgoldenrod', size=22)),
                          x1=1, y1=ov['P_pv_install'][0], line=dict(color="darkgoldenrod", dash="dot"), opacity=0.5)
    
    max_timestep = max(day_length, 100)
    # Prediction Power Values
    subplot_fig.update_layout(title="",
                              yaxis=dict(title=''), barmode='overlay')
    subplot_fig.update_xaxes(tickformat='', griddash="dot", title='', range=[-0.4, day_length+0.4],
                             tickvals=[i for i in range(0, max_timestep, 4)], tickfont=dict(size=22),
                             ticktext=[str(int(i/4)%24) for i in range(0, max_timestep, 4)], 
                             showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2)

    # For plot export: w(1280)xh(720), w(1920)xh(1080)
    # For better overview in jupyter: w(850)xh(650)
    plot_width = 1080
    plot_height = 750

    if model == 'model3' or model == 'model4':
        max_p = max(grid_power.max(), building_od.max())
        min_p = min(-max_p, grid_power.min())
        max_p_2 = max(pv_power.max(), total_ev_p.max(), battery_p.max(), ov['P_battery_MAX'][0])
        min_p_2 = min(-max_p_2, total_ev_p.min(), battery_p.min())
        delta_low = 45
        delta_low_2 = 19.5
    else:
        max_p = max(grid_power.max(), total_ev_p.max(), building_od.max())
        min_p = min(-max_p, grid_power.min())
        max_p_2 = max(pv_power.max(), total_ev_p.max(), battery_p.max())
        min_p_2 = min(-max_p_2, total_ev_p.min(), battery_p.min())
        delta_low = 23
        delta_low_2 = 0
    
    if model == 'model2':
        delta_low = 21
        delta_low_2 = 2
    
    if model == 'model3':
        delta_low = 44
        delta_low_2 = 23
    
    power_margin_high = int(round(max_p/10)*10)+10
    power_margin_low = int(round(min_p/10)*10)+delta_low
    power_ticks = int(max(power_margin_high, abs(power_margin_low))/5)
    
    power_margin_2_high = int(round(max_p_2/10)*10)+10
    power_margin_2_low = int(round(min_p_2/10)*10)+delta_low_2
    power_ticks_2 = int(max(power_margin_2_high, abs(power_margin_2_low))/5)
#     max_tariff = day_tariff.max()
#     tariff_margin = int(max_tariff)+0.25

    subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman",
                              title=dict(xanchor="center", x=0.5, font_size=24, y=0.99), 
                              showlegend=True, coloraxis=dict(colorscale=[[0, 'crimson'], [0.5, 'lightgrey'], 
                                                                          [1, 'grey']], 
                                                              colorbar=dict(title=dict(text='', side='right'))), 
                              barmode='stack',
                              legend=dict(x=0.5, orientation='h', yanchor='bottom', font_size=20, entrywidth=0, y=1.02, 
                                          xanchor='center'), scattermode='overlay',
                              yaxis=dict(tickformat=" ,", range=[power_margin_low, power_margin_high], dtick=power_ticks,
                                         tickfont=dict(size=22),
                                         showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2),
                              yaxis2=dict(tickformat=" ,", overlaying='y', tickfont=dict(size=22),
                                          range=[power_margin_2_low, power_margin_2_high], 
                                          dtick=power_ticks_2, anchor='free', autoshift=True, shift=2, side='right',
                                          showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2))
#                               yaxis2=dict(tickformat=" ,.0%", overlaying='y', anchor='free', nticks=11, dtick=0.05, 
#                                           tickmode='array', tickvals=[str(i/100) for i in range(0, 110, 25)], 
#                                           autoshift=True, shift=2, side='right', range=[-1.25, 1.25],
#                                           showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2))
#                               yaxis3=dict(overlaying='y',
#                                           range=[0, tariff_margin], visible=False))

#     config = {'locales': {'en': {'format': {'currency': [" € ", ""]}}}}
#     subplot_fig.show(config=config)
#     subplot_fig.show()
    if not os.path.exists(f"plots/{model}"):
        os.mkdir(f"plots/{model}")

    subplot_fig.write_image(f"plots/{model}/{model}_all_powers_day_{day}.png")

    del max_timestep, plot_width, plot_height

In [88]:
def plot_days_range_all_power_predictions(first_day=0, last_day=0, model=''):
    for d in range(first_day, last_day + 1, 1):
        plot_single_day_all_power_predictions(day=d, model=model)
    print('------------------------------------\n'
          'Finished plotting days predicted all powers.\n'
          '------------------------------------\n')

## Plot everything

In [89]:
print('Checkpoint 00: All data loaded successfully.', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
# plot_days_range_initial_info(first_day=18, last_day=18, model=model)
print('Checkpoint 01: Plotted days initial info successfully.', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))

Checkpoint 00: All data loaded successfully. 2023-09-21 18:14:23
Checkpoint 01: Plotted days initial info successfully. 2023-09-21 18:14:23


In [90]:
# plot_days_range_power_predictions(first_day=18, last_day=18, model=model)
print('Checkpoint 04: Plotted charging powers successfully.', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
# plot_days_range_battery_predictions(first_day=18, last_day=18, model=model)
print('Checkpoint 05: Plotted battery successfully.', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
# plot_days_range_grid_cost_predictions(first_day=18, last_day=18, model=model)
print('Checkpoint 07: Plotted cost successfully.', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
# plot_days_range_all_power_predictions(first_day=18, last_day=18, model=model)
print('Checkpoint 08: Plotted all powers successfully.', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
print('\n\n------------------------------------------------------')
print('------------------------------------------------------')
print('Checkpoint 09: Plotted everything successfully.', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))

Checkpoint 04: Plotted charging powers successfully. 2023-09-21 18:14:23
Checkpoint 05: Plotted battery successfully. 2023-09-21 18:14:23
Checkpoint 07: Plotted cost successfully. 2023-09-21 18:14:23
Checkpoint 08: Plotted all powers successfully. 2023-09-21 18:14:23


------------------------------------------------------
------------------------------------------------------
Checkpoint 09: Plotted everything successfully. 2023-09-21 18:14:23


## TO-DO:

Costs and investment, comparison between models, average costs per day... + grid tariff

In [91]:
high_tariff

0.329053

In [92]:
low_tariff

0.195422

In [93]:
low_tariff_data = ~temp_data_market
high_tariff_data = temp_data_market

In [94]:
low_tariff_data = low_tariff_data * low_tariff
high_tariff_data = high_tariff_data * high_tariff

In [95]:
tariff_cost = high_tariff_data + low_tariff_data
tariff_cost

tariff
0      0.195422
1      0.195422
2      0.195422
3      0.195422
4      0.195422
...         ...
35035  0.195422
35036  0.195422
35037  0.195422
35038  0.195422
35039  0.195422

[35040 rows x 1 columns]

In [96]:
building_df

Building Demand  Day
0                 12.8    0
1                 13.0    0
2                 12.8    0
3                 13.2    0
4                 13.4    0
...                ...  ...
35035             14.8  364
35036             14.8  364
35037             14.6  364
35038             14.2  364
35039             13.8  364

[35040 rows x 2 columns]

In [97]:
building_df.loc[building_df['Building Demand'] == building_df['Building Demand'].max(), :]

Building Demand  Day
1772            118.0   18

In [98]:
building_net_present_value = 1176849.00

In [99]:
building_net_present_value

1176849.0

In [100]:
optimised_costs = dict()
optimised_monthly_peak_p = dict()

In [101]:
file_path = f"data/building_data_2016-costs.xlsx"
building_sheet = pd.read_excel(file_path, sheet_name=None)
monthly_building_demand = building_sheet['skalirano'][['Peak power']].iloc[0:12]
    
# del building_sheet

In [102]:
monthly_building_demand

Peak power
0        118.0
1         83.0
2         78.2
3         67.4
4         62.0
5         79.8
6        100.6
7         83.2
8         84.0
9         80.0
10        93.4
11        97.6

In [103]:
for model in model_names:
    file_path = f"{results_directory}/{model}/{nanogrid_optimised_variables_file}"
    optimised_vars = pd.read_excel(file_path, sheet_name=None)
    optimised_costs[model] = optimised_vars['Optimal variables'][['P_pv_install', 'binary_pv', 'E_battery_capacity', 
                                                            'binary_battery', 'P_battery_MAX', 'P_contracted', 
                                                            'P_cs_contracted', 'C_total', 'C_invest', 'C_ee_operational', 
                                                            'C_ee_annual', 'C_profit_annual', 'C_profit', 'C_maintenance', 
                                                            'C_pv_maintenance', 'C_battery_maintenance', 'C_pl_maintenance', 
                                                            'C_loan', 'C_annuity', 'C_battery_replacement']]
    optimised_monthly_peak_p[model] = optimised_vars['Optimal monthly variables'][['P_grid_max']]
    
del optimised_vars

In [104]:
optimised_monthly_peak_p

{'model1':     P_grid_max
 0    32.284971
 1    34.752971
 2    40.460971
 3    43.954971
 4    41.826971
 5    40.521036
 6    39.486000
 7    39.872754
 8    38.663094
 9    34.396800
 10   25.422971
 11   24.684971,
 'model2':     P_grid_max
 0       36.332
 1       38.800
 2       44.508
 3       48.002
 4       45.874
 5       43.380
 6       42.334
 7       42.326
 8       42.264
 9       35.762
 10      29.470
 11      28.732,
 'model3':     P_grid_max
 0    73.587466
 1    55.146295
 2    55.281113
 3    51.908868
 4    44.025065
 5    54.352870
 6    59.740675
 7    42.586915
 8    55.357040
 9    54.916584
 10   54.281306
 11   58.789049,
 'model4':     P_grid_max
 0    74.420507
 1    55.762344
 2    59.293363
 3    56.324608
 4    44.699162
 5    59.599242
 6    65.329013
 7    40.779722
 8    58.738701
 9    57.530455
 10   59.288930
 11   60.402383}

In [105]:
optimised_costs

{'model1':    P_pv_install  binary_pv  E_battery_capacity  binary_battery  P_battery_MAX  \
 0          60.0          1           40.380115               1      10.095029   
 
    P_contracted  P_cs_contracted       C_total      C_invest  \
 0     43.954971        43.954971  39350.004648  81176.124087   
 
    C_ee_operational  C_ee_annual  C_profit_annual       C_profit  \
 0     127051.195551  8926.220411     15977.034712  227408.832396   
 
    C_maintenance  C_pv_maintenance  C_battery_maintenance  C_pl_maintenance  \
 0   25655.601808              1800             161.520461               240   
 
          C_loan    C_annuity  C_battery_replacement  
 0  31644.283419  4505.434049            1231.632178  ,
 'model2':    P_pv_install  binary_pv  E_battery_capacity  binary_battery  P_battery_MAX  \
 0          60.0          1              24.192               1          6.048   
 
    P_contracted  P_cs_contracted       C_total      C_invest  \
 0        48.002           48.002  345

In [106]:
subplot_fig = go.Figure()

colour_lines = ['rgba(0, 206, 209, 1)', 'rgba(0, 206, 29, 1)', 
                'rgba(255, 140, 0, 1)', 'rgba(105, 105, 105, 1)', 
                'crimson', 'slateblue']
markers = ['circle', 'square', 'cross', 'diamond', '0', '0', 'diamond']
dash_types = ['solid', 'dot', 'dashdot', 'dash']
line_widths = [1.5, 1.5, 1.5, 1.5, 1.5, 1.5, 1.5]

for i, model in enumerate(model_names):
    if i + 1 == 1:
        x = list(monthly_building_demand.index)
        y = monthly_building_demand['Peak power']+optimised_monthly_peak_p['model1']['P_grid_max']
    elif i + 1 == 2:
        x = list(monthly_building_demand.index)
        y = monthly_building_demand['Peak power']+optimised_monthly_peak_p['model2']['P_grid_max']
    else:
        x = list(optimised_monthly_peak_p[model].index)
        y=optimised_monthly_peak_p[model]['P_grid_max']
    
    subplot_fig.add_trace(go.Scatter(
        x=x, y=y,
        line_color=colour_lines[i], line_dash=dash_types[0],
        name=f'Model {i+1}: Charging Station + Building', mode='lines',
        legendgroup=f'{model} total', line_shape='hvh',
        showlegend=True, line_width=line_widths[i],
        marker=dict(size=0, symbol=markers[i])
    ))

i = 4
x = list(monthly_building_demand.index)
subplot_fig.add_trace(go.Scatter(
        x=x, y=monthly_building_demand['Peak power'],
        line_color=colour_lines[i], line_dash=dash_types[0],
        name=f'Building only', line_shape='hvh', mode='lines',
        legendgroup=f'{model} Building demand',
        showlegend=True, line_width=line_widths[i],
        marker=dict(size=0, symbol=markers[i])
    ))

# i = 5
# x = list(monthly_building_demand.index)
# y = monthly_building_demand['Peak power']+optimised_monthly_peak_p['model1']['P_grid_max']
# subplot_fig.add_trace(go.Scatter(
#         x=x, y=y,
#         line_color=colour_lines[i], line_dash=dash_types[0],
#         name=f'Model 1: Charging Station + Building', mode='lines',
#         legendgroup=f'Model 1 with Building demand', line_shape='hvh',
#         showlegend=True, line_width=line_widths[i],
#         marker=dict(size=0, symbol=markers[i])
#     ))

# i = 6
# x = list(monthly_building_demand.index)
# y = monthly_building_demand['Peak power']+optimised_monthly_peak_p['model2']['P_grid_max']
# subplot_fig.add_trace(go.Scatter(
#         x=x, y=y,
#         line_color=colour_lines[i], line_dash=dash_types[0],
#         name=f'Model 2: Charging Station + Building', mode='lines',
#         legendgroup=f'Model 2 with Building demand', line_shape='hvh',
#         showlegend=True, line_width=line_widths[i],
#         marker=dict(size=0, symbol=markers[i])
#     ))

subplot_fig.add_annotation(x=-0.08, y=0.5, text="<b>Peak Power [kW]</b>", xanchor='left', yanchor='middle', 
                           textangle=-90, xref="paper", yref="paper", font_size=24, showarrow=False)
# subplot_fig.add_annotation(x=1.07, y=0.7, text="<b>State of Charge</b>", xanchor='left', yanchor='middle', 
# textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
subplot_fig.add_annotation(x=0.5, y=-0.12, text="<b>Month</b>", textangle=0, xref="paper", yref="paper", font_size=24, 
                           showarrow=False)

# max_timestep = max(day_length, 100)
# # Prediction Power Values
# subplot_fig.update_layout(title="",
#                           yaxis=dict(title=''), barmode='overlay')
subplot_fig.update_xaxes(tickformat='', griddash="dot", title='', range=[-0.4, 11.4],
                         tickvals=[i for i in range(0, 12, 1)], 
                         ticktext=[str(i+1) for i in range(0, 12, 1)], 
                         showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2)
# ticks='outside', title='<b>Day in a year</b>',


# # For plot export: w(1280)xh(720), w(1920)xh(1080)
# # For better overview in jupyter: w(850)xh(650)
plot_width = 980
plot_height = 650

# if model == 'model3' or model == 'model4':
#     max_p = max(grid_power.max(), pv_power.max(), total_ev_p.max(), battery_p.max(), battery_soc.max(), 
# building_od.max())
# else:
#     max_p = max(grid_power.max(), pv_power.max(), total_ev_p.max(), battery_p.max(), battery_soc.max())

# power_margin = int(round(max_p/10)*10)+10
# power_ticks = int(power_margin/5)
# #     max_tariff = day_tariff.max()
# #     tariff_margin = int(max_tariff)+0.25

# subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman",
#                           title=dict(xanchor="center", x=0.5, font_size=24, y=0.99), 
#                           showlegend=True, coloraxis=dict(colorscale=[[0, 'crimson'], [0.5, 'lightgrey'], [1, 'grey']], 
#                                                           colorbar=dict(title=dict(text='', side='right'))), 
# barmode='stack',
#                           legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'), 
# scattermode='overlay',
#                           yaxis=dict(tickformat=" ,", range=[-power_margin, power_margin], dtick=power_ticks, 
# showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2),
#                           yaxis2=dict(tickformat=" ,.0%", overlaying='y', anchor='free', nticks=11, dtick=0.05, 
#                                       tickmode='array', tickvals=[str(i/100) for i in range(0, 110, 25)], 
# autoshift=True, 
#                                       shift=2, side='right', range=[-1.25, 1.25],
#                                       showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2))
# #                               yaxis3=dict(overlaying='y',
# #                                           range=[0, tariff_margin], visible=False))
subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman", 
                          scattermode='overlay', 
                          legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, font_size=22,
                                      y=1.02, xanchor='center'),
                          yaxis=dict(tickfont=dict(size=22)), xaxis=dict(tickfont=dict(size=22)))

# subplot_fig.show()
if not os.path.exists(f"plots"):
    os.mkdir(f"plots")

subplot_fig.write_image(f"plots/monthly_peak_powers_per_model_variant.png")

del plot_width, plot_height

In [107]:
subplot_fig = go.Figure()
model_line_colors = ['black', 'black', 'crimson', 'crimson', 'crimson', 'crimson']
line_styles =['dash', 'solid', 'dashdot', 'solid']

models_size = len(model_names)

for i, model in enumerate(model_names):
    if i < 2:
        continue
    total_cost = optimised_costs[model]['C_total']
    total_investment_cost = optimised_costs[model]['C_invest']
    total_loan_cost = optimised_costs[model]['C_loan']
    total_maintenance_cost = optimised_costs[model]['C_maintenance']
    total_operational_cost = optimised_costs[model]['C_ee_operational']
    total_replacement_cost = optimised_costs[model]['C_battery_replacement']
    total_profit = -optimised_costs[model]['C_profit']

    subplot_fig.add_bar(y=[i], x=total_investment_cost, showlegend=False, yaxis='y', width=0.8, legendgroup='Investment',
                        marker=dict(color='gold', opacity=0.9, line_width=0), name='Total Investment Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_loan_cost, showlegend=False, yaxis='y', width=0.8, legendgroup='Loan',
                        marker=dict(color='darkturquoise', opacity=0.9, line_width=0), name='Total Loan Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_maintenance_cost, showlegend=False, yaxis='y', width=0.8, legendgroup='Maintenance',
                        marker=dict(color='teal', opacity=0.9, line_width=0), name='Total Maintenance Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_operational_cost, showlegend=False, yaxis='y', width=0.8, legendgroup='Operational',
                        marker=dict(color='orange', opacity=0.8, line_width=0), name='Total Operational Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_replacement_cost, showlegend=False, yaxis='y', width=0.9, legendgroup='Replacement',
                        marker=dict(color='crimson', opacity=0.8, line_width=0), name='Total Replacement Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_profit, showlegend=False, yaxis='y', width=0.8, legendgroup='Profit',
                        marker=dict(color='dimgrey', pattern=dict(shape='/', fillmode='replace', size=10), 
                                    opacity=0.7, line_width=1, line_color='dimgrey'), 
                        name='Total Profit', orientation='h')

    subplot_fig.add_scatter(x=total_cost, y=[i], line_shape='linear', name='Total Cost', mode='markers',
                            marker=dict(size=10, symbol='diamond', line=dict(width=1.5), color='black'), 
                            line=dict(color='rgba(0,0,0,0.7)'),
                            showlegend=False, yaxis='y', legendgroup='Total Cost')
    
    subplot_fig.add_vline(x=total_cost[0], line_width=1.7, line_color=model_line_colors[i], opacity=0.7,
                          line_dash=line_styles[i], annotation_text="", 
                          annotation_position="top left", annotation_font_size=18, annotation_font_color="dimgrey",
                          annotation_opacity=0.5)

for i, model in enumerate(model_names):
    if i == 2:
        break
        
    only_building_cost = building_net_present_value
    total_cost = optimised_costs[model]['C_total'] + only_building_cost
    total_investment_cost = optimised_costs[model]['C_invest']
    total_loan_cost = optimised_costs[model]['C_loan']
    total_maintenance_cost = optimised_costs[model]['C_maintenance']
    total_operational_cost = optimised_costs[model]['C_ee_operational']
    total_replacement_cost = optimised_costs[model]['C_battery_replacement']
    total_profit = -optimised_costs[model]['C_profit']

    subplot_fig.add_bar(y=[i], x=[only_building_cost], showlegend=(not i), yaxis='y', width=0.8, 
                        legendgroup='Building only',
                        marker=dict(color='black', opacity=0.9, line_width=0), name='Total Building Only Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_investment_cost, showlegend=(not i), yaxis='y', width=0.8, 
                        legendgroup='Investment',
                        marker=dict(color='gold', opacity=0.9, line_width=0), name='Total Investment Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_loan_cost, showlegend=(not i), yaxis='y', width=0.8, legendgroup='Loan',
                        marker=dict(color='darkturquoise', opacity=0.9, line_width=0), name='Total Loan Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_maintenance_cost, showlegend=(not i), yaxis='y', width=0.8, 
                        legendgroup='Maintenance',
                        marker=dict(color='teal', opacity=0.9, line_width=0), name='Total Maintenance Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_operational_cost, showlegend=(not i), yaxis='y', width=0.8, 
                        legendgroup='Operational',
                        marker=dict(color='orange', opacity=0.8, line_width=0), name='Total Operational Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_replacement_cost, showlegend=(not i), yaxis='y', width=0.9, 
                        legendgroup='Replacement',
                        marker=dict(color='crimson', opacity=0.8, line_width=0), name='Total Replacement Cost', 
                        orientation='h')
    subplot_fig.add_bar(y=[i], x=total_profit, showlegend=(not i), yaxis='y', width=0.8, legendgroup='Profit',
                        marker=dict(color='dimgrey', pattern=dict(shape='/', fillmode='replace', size=10), 
                                    opacity=0.7, line_width=1, line_color='dimgrey'), 
                        name='Total Profit', orientation='h')

    subplot_fig.add_scatter(x=total_cost, y=[i], line_shape='linear', name='Total Cost', mode='markers',
                            marker=dict(size=10, symbol='diamond', line=dict(width=1.5), color='black'), 
                            line=dict(color='rgba(0,0,0,0.7)'),
                            showlegend=(not i), yaxis='y', legendgroup='Total Cost')
    
    subplot_fig.add_vline(x=total_cost[0], line_width=1.7, line_color=model_line_colors[i], opacity=0.7,
                          line_dash=line_styles[i], annotation_text="", 
                          annotation_position="top left", annotation_font_size=16, annotation_font_color="dimgrey",
                          annotation_opacity=0.5)

subplot_fig.add_bar(y=[i+2], x=[only_building_cost], yaxis='y', width=0.8, legendgroup='Building only', showlegend=False, 
                    marker=dict(color='black', opacity=0.9, line_width=0), name='Total Building Only Cost', 
                    orientation='h')

subplot_fig.add_annotation(x=-0.08, y=0.5, text="<b>Optimisation Models</b>", xanchor='left', yanchor='middle', 
                           textangle=-90, xref="paper", yref="paper", font_size=22, showarrow=False)
subplot_fig.add_annotation(x=0.5, y=-0.15, text="<b>Cost/Profit [€]</b>", textangle=0, xref="paper", yref="paper", 
                           font_size=22, showarrow=False)

subplot_fig.update_layout(title="",
                          yaxis=dict(title=''), barmode='overlay')
subplot_fig.update_yaxes(tickformat='', griddash="dot", title='',
                         tickvals=[i for i in range(0, 7, 1)],
                         ticktext=['Model 1', 'Model 2', 'Model 3', 'Model 4', 
                                   'Building Only'])

# For plot export: w(1280)xh(720), w(1920)xh(1080)
# For better overview in jupyter: w(850)xh(650)
plot_width = 1480
plot_height = 500


# total_pen1_max = total_cost.max()
ytype = 'log' if 0 > 100000 else 'linear'
# ymax_margin = 6 if ytype == 'log' else round(total_pen1_max + total_pen1_max/10)
# yyaxistext = '- log scale' if ytype == 'log' else ''
# ydtick = 1 if ytype == 'log' else 5
subplot_fig.update_layout(height=plot_height, width=plot_width, title=dict(xanchor="center", x=0.5, font_size=24, y=0.99),
                          font_family="Computer Modern Roman",
                          showlegend=True, barmode='stack',
                          legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, y=1.01, xanchor='center',
                                      font_size=20), 
                          scattermode='overlay',
                          xaxis=dict(tickformat=" ,~", nticks=15, type=f'{ytype}', tickfont=dict(size=20)),
                          yaxis=dict(tickfont=dict(size=20)))


# subplot_fig.show()

if not os.path.exists(f"plots"):
    os.mkdir(f"plots")

subplot_fig.write_image(f"plots/costs_and_profits_per_model_variant.png")

del plot_width, plot_height

In [108]:
optimised_cost_profit = dict()
cost_profit_predictions = dict()

In [109]:
for model in model_names:
    file_path = f"{results_directory}/{model}/{nanogrid_optimised_variables_file}"
    optimised_vars = pd.read_excel(file_path, sheet_name=None)
    optimised_cost_profit = optimised_vars['15-min optimal data for 1 year']
    tdf = optimised_cost_profit['C_ee_hourly'] - optimised_cost_profit['C_profit_hourly']
    cost_profit_predictions[model] = pd.DataFrame(tdf)
    cost_profit_predictions[model].columns = ['Cost/Profit']
    cost_profit_predictions[model]['Day'] = cost_profit_predictions[model].index // 96
del optimised_vars, tdf, file_path, optimised_cost_profit

In [110]:
cost_profit = dict()

In [111]:
for model in model_names:
    mean_cost_profit = list()
    min_cost_profit = list()
    max_cost_profit = list()
    sum_cost_profit = list()

    i = 0
    max_day = cost_profit_predictions[model]['Day'].max() + 1
    while i < max_day:
        temporary = cost_profit_predictions[model].loc[cost_profit_predictions[model]['Day'] == i, :].describe()
        max_cost_profit.append(temporary['Cost/Profit']['max'])
        mean_cost_profit.append(temporary['Cost/Profit']['mean'])
        min_cost_profit.append(temporary['Cost/Profit']['min'])
        sum_cost_profit.append(cost_profit_predictions[model].loc[cost_profit_predictions[model]['Day'] == i, :]['Cost/Profit'].sum())
        i = i + 1

    cost_profit[model] = pd.DataFrame({'Min Cost/Profit': min_cost_profit, 'Mean Cost/Profit': mean_cost_profit, 
                                       'Max Cost/Profit': max_cost_profit, 'Sum Cost/Profit': sum_cost_profit})
    
del min_cost_profit, mean_cost_profit, max_cost_profit, temporary, max_day, i, sum_cost_profit

In [112]:
cost_profit

{'model1':      Min Cost/Profit  Mean Cost/Profit  Max Cost/Profit  Sum Cost/Profit
 0           0.000000          0.245720         1.577298        23.589138
 1           0.000000          0.913048         2.372054        87.652606
 2           0.000000          0.185277         1.577298        17.786631
 3           0.000000          0.544992         1.825440        52.319233
 4           0.000000          0.562718         1.979126        54.020938
 ..               ...               ...              ...              ...
 360        -0.785377          0.162769         1.205997        15.625855
 361         0.000000          0.338402         1.205997        32.486599
 362        -1.411260         -0.232060         0.053172       -22.277768
 363        -1.411260         -0.282509         0.008658       -27.120818
 364         0.000000          0.564662         2.030666        54.207580
 
 [365 rows x 4 columns],
 'model2':      Min Cost/Profit  Mean Cost/Profit  Max Cost/Profit  Sum Cos

In [113]:
# subplot_fig = go.Figure()
subplot_fig = make_subplots(
        rows=len(model_names),
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.04,
        specs=[[{'secondary_y': True}]]*len(model_names)
    )

# day_length = len(cost[0])
# t = day_length/24
# subplot_fig.add_vrect(x0=0, x1=7*t, fillcolor='grey', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=3.5/24, y=0.05, text="Low Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='dimgrey'), showarrow=False)
# subplot_fig.add_vrect(x0=7*t, x1=20*t, fillcolor='gold', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=13.5/24, y=0.05, text="Peak Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='goldenrod'), showarrow=False)
# subplot_fig.add_vrect(x0=20*t, x1=day_length, fillcolor='grey', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=22/24, y=0.05, text="Low Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='dimgrey'), showarrow=False)

colour_fills = ['rgba(0, 206, 209, 0.2)', 'rgba(255, 215, 0, 0.2)', 'rgba(255, 165, 32, 0.3)', 'rgba(105, 105, 105, 0.2)']
colour_lines = ['rgba(0, 206, 209, 1)', 'rgba(255, 215, 0, 1)', 'rgba(255, 165, 32, 1)', 'rgba(105, 105, 105, 1)']
# pattern_fills = ['', '/', '', ''] rgb(255, 165, 0) rgb(218, 165, 32) rgba(255, 215, 0, 1)
markers = ['circle', 'square', 'cross', 'diamond']
dash_types = ['solid', 'dot', 'dashdot', 'dash']
line_widths = [0.5, 1.5, 2.5, 3.5]

for i, model in enumerate(model_names):
    x = list(cost_profit[model].index)
#     y_upper = cost_profit[model]['Max Cost/Profit']
#     y_lower = cost_profit[model]['Min Cost/Profit']
    
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=y_upper,
#         line_color='rgba(0,0,0,0)',
#         name=f'{model} average cost(+)/profit(-)',
#         showlegend=False,
#         legendgroup=f'{model}'
#     ))
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=y_lower,
#         fillcolor=colour_fills[i],
#         opacity=0.2,
#         line_color='rgba(0,0,0,0)',
#         name=f'{model} average cost(+)/profit(-)',
#         fill='tonexty',
#         showlegend=True,
#         legendgroup=f'{model}'
#     ))
#     subplot_fig.update_traces(mode='lines')
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=cost_profit[model]['Mean Cost/Profit'],
#         line_color=colour_lines[i], line_dash=dash_types[i],
#         name=f'{model} average cost(+)/profit(-)',
#         legendgroup=f'{model}',
#         showlegend=False,
#     ))
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=cost_profit[model]['Sum Cost/Profit'],
#         line_color=colour_lines[i], line_dash=dash_types[0],
#         name=f'{model} total cost(+)/profit(-)',
#         legendgroup=f'{model} total', row=i, column=1,
#         showlegend=True, line_width=line_widths[i],
#         marker=dict(size=0, symbol=markers[i])
#     ))
    subplot_fig.add_scatter(
        x=x, y=cost_profit[model]['Min Cost/Profit'],
        line_color=colour_lines[i], line_dash=dash_types[1],
        name=f'{model} Min cost(+)/profit(-)',
        legendgroup=f'{model} Min',
        fill='tozeroy', row=i+1, col=1,
        showlegend=True, line_width=line_widths[0],
        marker=dict(size=0, symbol=markers[i])
    )
    subplot_fig.add_scatter(
        x=x, y=cost_profit[model]['Max Cost/Profit'],
        line_color=colour_lines[i], line_dash=dash_types[1],
        name=f'{model} Max cost(+)/profit(-)',
        legendgroup=f'{model} Max',
        fill='tozeroy', 
        row=i+1, col=1,
        showlegend=True, line_width=line_widths[0],
        marker=dict(size=0, symbol=markers[i])
    )
    subplot_fig.add_scatter(
        x=x, y=cost_profit[model]['Mean Cost/Profit'],
        line_color='crimson', line_dash=dash_types[0],
        name=f'{model} Mean cost(+)/profit(-)',
        legendgroup=f'{model} Mean', row=i+1, col=1,
        showlegend=True, line_width=line_widths[1],
        marker=dict(size=0, symbol=markers[i])
    )
#     break
    
#     number_of_days = cost_predictions['Day'].max()+1
#     for day in range(number_of_days):
        
# number_of_days = cost_predictions['Day'].max()+1
# for day in range(number_of_days):
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model1'].loc[cost_profit_predictions['model1']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='blue',
#         line_color='blue'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model2'].loc[cost_profit_predictions['model2']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='green',
#         line_color='green'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model3'].loc[cost_profit_predictions['model3']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='red',
#         line_color='red'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model4'].loc[cost_profit_predictions['model4']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='dimgrey',
#         line_color='dimgrey'))

# y_lower = y_lower[::-1]
# subplot_fig.add_trace(go.Scatter(
#     x=x+x_rev,
#     y=y_upper+y_lower,
#     fill='tonextx',
#     fillcolor='rgba(0,176,246,0.2)',
#     line_color='rgba(0,0,0,1)',
#     name='Premium',
#     showlegend=False,))


# grid_power = grid_p[day]['Grid Power Value']
# # day_tariff = costs_predictions['Electricity Day Tariffs']


# subplot_fig.add_hline(y=ov['P_battery_MAX'][0], line_width=1.5, line_color="crimson", opacity=0.5,
#                       line_dash="dot", annotation_text="<i>MAX Battery Power</i>", 
#                       annotation_position="top left", annotation_font_size=12, annotation_font_color="crimson",
#                       annotation_opacity=0.5)

# subplot_fig.add_scatter(x=cost[day].index, y=battery_soc, line_shape='linear', name='Battery SOC', mode='lines+markers',
#                         marker=dict(size=4, symbol='square', line=dict(width=0), color='dimgrey', coloraxis='coloraxis'), line=dict(color='dimgrey'),
#                         showlegend=True, yaxis='y2', legendgroup='SOC')
# # # Electricity Day Tariff
# # subplot_fig.add_scatter(x=costs_predictions.index, y=day_tariff, line_shape='hv', name='Dnevna tarifa električne energije', mode='lines+markers',
# #                         marker=dict(size=0, symbol='circle', line=dict(width=0), color='teal', coloraxis='coloraxis'), line=dict(color='teal'),
# #                         showlegend=True, yaxis='y2', legendgroup='Day Tariff')

# subplot_fig.add_annotation(x=-0.08, y=0.5, text="<b>Power [kW]</b>", xanchor='left', yanchor='middle', textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
# subplot_fig.add_annotation(x=1.07, y=0.7, text="<b>State of Charge</b>", xanchor='left', yanchor='middle', textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
# subplot_fig.add_annotation(x=0.5, y=-0.1, text="<b>Timestep (Hour) in a Day</b>", textangle=0, xref="paper", yref="paper", font_size=14, showarrow=False)

# max_timestep = max(day_length, 100)
# # Prediction Power Values
# subplot_fig.update_layout(title="",
#                           yaxis=dict(title=''), barmode='overlay')
# subplot_fig.update_xaxes(tickformat='', griddash="dot", title='', range=[-0.4, day_length+0.4],
#                          tickvals=[i for i in range(0, max_timestep, 4)], 
#                          ticktext=[str(int(i/4)%24) for i in range(0, max_timestep, 4)], 
#                          showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2)

# # For plot export: w(1280)xh(720), w(1920)xh(1080)
# # For better overview in jupyter: w(850)xh(650)
plot_width = 980
plot_height = 950

# if model == 'model3' or model == 'model4':
#     max_p = max(grid_power.max(), pv_power.max(), total_ev_p.max(), battery_p.max(), battery_soc.max(), building_od.max())
# else:
#     max_p = max(grid_power.max(), pv_power.max(), total_ev_p.max(), battery_p.max(), battery_soc.max())

# power_margin = int(round(max_p/10)*10)+10
# power_ticks = int(power_margin/5)
# #     max_tariff = day_tariff.max()
# #     tariff_margin = int(max_tariff)+0.25

# subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman",
#                           title=dict(xanchor="center", x=0.5, font_size=24, y=0.99), 
#                           showlegend=True, coloraxis=dict(colorscale=[[0, 'crimson'], [0.5, 'lightgrey'], [1, 'grey']], 
#                                                           colorbar=dict(title=dict(text='', side='right'))), barmode='stack',
#                           legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'), scattermode='overlay',
#                           yaxis=dict(tickformat=" ,", range=[-power_margin, power_margin], dtick=power_ticks, showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2),
#                           yaxis2=dict(tickformat=" ,.0%", overlaying='y', anchor='free', nticks=11, dtick=0.05, 
#                                       tickmode='array', tickvals=[str(i/100) for i in range(0, 110, 25)], autoshift=True, 
#                                       shift=2, side='right', range=[-1.25, 1.25],
#                                       showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2))
# #                               yaxis3=dict(overlaying='y',
# #                                           range=[0, tariff_margin], visible=False))
subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman", 
                          scattermode='overlay', 
                          legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'))

subplot_fig.show()
#     if not os.path.exists(f"plots/{model}/all_powers"):
#         os.mkdir(f"plots/{model}/all_powers")

#     subplot_fig.write_image(f"plots/{model}/all_powers/all_powers_day_{day}.png")

# del max_timestep, plot_width, plot_height

In [114]:
# subplot_fig = go.Figure()
subplot_fig = make_subplots(
        rows=len(model_names),
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.04,
        specs=[[{'secondary_y': True}]]*len(model_names)
    )

# day_length = len(cost[0])
# t = day_length/24
# subplot_fig.add_vrect(x0=0, x1=7*t, fillcolor='grey', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=3.5/24, y=0.05, text="Low Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='dimgrey'), showarrow=False)
# subplot_fig.add_vrect(x0=7*t, x1=20*t, fillcolor='gold', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=13.5/24, y=0.05, text="Peak Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='goldenrod'), showarrow=False)
# subplot_fig.add_vrect(x0=20*t, x1=day_length, fillcolor='grey', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=22/24, y=0.05, text="Low Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='dimgrey'), showarrow=False)

colour_fills = ['rgba(0, 206, 209, 0.2)', 'rgba(255, 215, 0, 0.2)', 'rgba(255, 165, 32, 0.3)', 'rgba(105, 105, 105, 0.2)']
colour_lines = ['rgba(0, 206, 209, 1)', 'rgba(255, 215, 0, 1)', 'rgba(255, 165, 32, 1)', 'rgba(105, 105, 105, 1)']
# pattern_fills = ['', '/', '', ''] rgb(255, 165, 0) rgb(218, 165, 32) rgba(255, 215, 0, 1)
markers = ['circle', 'square', 'cross', 'diamond']
dash_types = ['solid', 'dot', 'dashdot', 'dash']
line_widths = [0.5, 1.5, 2.5, 3.5]

for i, model in enumerate(model_names):
    x = list(cost_profit[model].index)
#     y_upper = cost_profit[model]['Max Cost/Profit']
#     y_lower = cost_profit[model]['Min Cost/Profit']
    
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=y_upper,
#         line_color='rgba(0,0,0,0)',
#         name=f'{model} average cost(+)/profit(-)',
#         showlegend=False,
#         legendgroup=f'{model}'
#     ))
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=y_lower,
#         fillcolor=colour_fills[i],
#         opacity=0.2,
#         line_color='rgba(0,0,0,0)',
#         name=f'{model} average cost(+)/profit(-)',
#         fill='tonexty',
#         showlegend=True,
#         legendgroup=f'{model}'
#     ))
#     subplot_fig.update_traces(mode='lines')
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=cost_profit[model]['Mean Cost/Profit'],
#         line_color=colour_lines[i], line_dash=dash_types[i],
#         name=f'{model} average cost(+)/profit(-)',
#         legendgroup=f'{model}',
#         showlegend=False,
#     ))
    subplot_fig.add_scatter(
        x=x, y=cost_profit[model]['Sum Cost/Profit'],
        line_color=colour_lines[i], line_dash=dash_types[0],
        name=f'{model} total cost(+)/profit(-)',
        legendgroup=f'{model} total', row=i+1, col=1,
        showlegend=True, line_width=line_widths[i],
        marker=dict(size=0, symbol=markers[i])
    )
#     break
    
#     number_of_days = cost_predictions['Day'].max()+1
#     for day in range(number_of_days):
        
# number_of_days = cost_predictions['Day'].max()+1
# for day in range(number_of_days):
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model1'].loc[cost_profit_predictions['model1']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='blue',
#         line_color='blue'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model2'].loc[cost_profit_predictions['model2']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='green',
#         line_color='green'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model3'].loc[cost_profit_predictions['model3']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='red',
#         line_color='red'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model4'].loc[cost_profit_predictions['model4']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='dimgrey',
#         line_color='dimgrey'))

# y_lower = y_lower[::-1]
# subplot_fig.add_trace(go.Scatter(
#     x=x+x_rev,
#     y=y_upper+y_lower,
#     fill='tonextx',
#     fillcolor='rgba(0,176,246,0.2)',
#     line_color='rgba(0,0,0,1)',
#     name='Premium',
#     showlegend=False,))


# grid_power = grid_p[day]['Grid Power Value']
# # day_tariff = costs_predictions['Electricity Day Tariffs']


# subplot_fig.add_hline(y=ov['P_battery_MAX'][0], line_width=1.5, line_color="crimson", opacity=0.5,
#                       line_dash="dot", annotation_text="<i>MAX Battery Power</i>", 
#                       annotation_position="top left", annotation_font_size=12, annotation_font_color="crimson",
#                       annotation_opacity=0.5)

# subplot_fig.add_scatter(x=cost[day].index, y=battery_soc, line_shape='linear', name='Battery SOC', mode='lines+markers',
#                         marker=dict(size=4, symbol='square', line=dict(width=0), color='dimgrey', coloraxis='coloraxis'), line=dict(color='dimgrey'),
#                         showlegend=True, yaxis='y2', legendgroup='SOC')
# # # Electricity Day Tariff
# # subplot_fig.add_scatter(x=costs_predictions.index, y=day_tariff, line_shape='hv', name='Dnevna tarifa električne energije', mode='lines+markers',
# #                         marker=dict(size=0, symbol='circle', line=dict(width=0), color='teal', coloraxis='coloraxis'), line=dict(color='teal'),
# #                         showlegend=True, yaxis='y2', legendgroup='Day Tariff')

# subplot_fig.add_annotation(x=-0.08, y=0.5, text="<b>Power [kW]</b>", xanchor='left', yanchor='middle', textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
# subplot_fig.add_annotation(x=1.07, y=0.7, text="<b>State of Charge</b>", xanchor='left', yanchor='middle', textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
# subplot_fig.add_annotation(x=0.5, y=-0.1, text="<b>Timestep (Hour) in a Day</b>", textangle=0, xref="paper", yref="paper", font_size=14, showarrow=False)

# max_timestep = max(day_length, 100)
# # Prediction Power Values
# subplot_fig.update_layout(title="",
#                           yaxis=dict(title=''), barmode='overlay')
# subplot_fig.update_xaxes(tickformat='', griddash="dot", title='', range=[-0.4, day_length+0.4],
#                          tickvals=[i for i in range(0, max_timestep, 4)], 
#                          ticktext=[str(int(i/4)%24) for i in range(0, max_timestep, 4)], 
#                          showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2)

# # For plot export: w(1280)xh(720), w(1920)xh(1080)
# # For better overview in jupyter: w(850)xh(650)
plot_width = 980
plot_height = 950

# if model == 'model3' or model == 'model4':
#     max_p = max(grid_power.max(), pv_power.max(), total_ev_p.max(), battery_p.max(), battery_soc.max(), building_od.max())
# else:
#     max_p = max(grid_power.max(), pv_power.max(), total_ev_p.max(), battery_p.max(), battery_soc.max())

# power_margin = int(round(max_p/10)*10)+10
# power_ticks = int(power_margin/5)
# #     max_tariff = day_tariff.max()
# #     tariff_margin = int(max_tariff)+0.25

# subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman",
#                           title=dict(xanchor="center", x=0.5, font_size=24, y=0.99), 
#                           showlegend=True, coloraxis=dict(colorscale=[[0, 'crimson'], [0.5, 'lightgrey'], [1, 'grey']], 
#                                                           colorbar=dict(title=dict(text='', side='right'))), barmode='stack',
#                           legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'), scattermode='overlay',
#                           yaxis=dict(tickformat=" ,", range=[-power_margin, power_margin], dtick=power_ticks, showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2),
#                           yaxis2=dict(tickformat=" ,.0%", overlaying='y', anchor='free', nticks=11, dtick=0.05, 
#                                       tickmode='array', tickvals=[str(i/100) for i in range(0, 110, 25)], autoshift=True, 
#                                       shift=2, side='right', range=[-1.25, 1.25],
#                                       showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2))
# #                               yaxis3=dict(overlaying='y',
# #                                           range=[0, tariff_margin], visible=False))
subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman", 
                          scattermode='overlay', 
                          legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'))

subplot_fig.show()
#     if not os.path.exists(f"plots/{model}/all_powers"):
#         os.mkdir(f"plots/{model}/all_powers")

#     subplot_fig.write_image(f"plots/{model}/all_powers/all_powers_day_{day}.png")

# del max_timestep, plot_width, plot_height

In [115]:
subplot_fig = go.Figure()

# day_length = len(cost[0])
# t = day_length/24
# subplot_fig.add_vrect(x0=0, x1=7*t, fillcolor='grey', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=3.5/24, y=0.05, text="Low Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='dimgrey'), showarrow=False)
# subplot_fig.add_vrect(x0=7*t, x1=20*t, fillcolor='gold', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=13.5/24, y=0.05, text="Peak Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='goldenrod'), showarrow=False)
# subplot_fig.add_vrect(x0=20*t, x1=day_length, fillcolor='grey', opacity=0.1, layer='above', line=dict(width=0))
# subplot_fig.add_annotation(x=22/24, y=0.05, text="Low Demand", xanchor='center', yanchor='middle', xref="paper", yref="paper", font=dict(size=14, color='dimgrey'), showarrow=False)

colour_fills = ['rgba(0, 206, 209, 0.2)', 'rgba(255, 215, 0, 0.2)', 'rgba(255, 165, 32, 0.3)', 'rgba(105, 105, 105, 0.2)']
colour_lines = ['rgba(0, 206, 209, 1)', 'rgba(255, 215, 0, 1)', 'rgba(255, 165, 32, 1)', 'rgba(105, 105, 105, 1)']
# pattern_fills = ['', '/', '', ''] rgb(255, 165, 0) rgb(218, 165, 32) rgba(255, 215, 0, 1)
markers = ['circle', 'square', 'cross', 'diamond']
dash_types = ['solid', 'dot', 'dashdot', 'dash']
line_widths = [1.5, 1.5, 1.5, 0.5]

for i, model in enumerate(model_names):
    x = list(cost_profit[model].index)
#     y_upper = cost_profit[model]['Max Cost/Profit']
#     y_lower = cost_profit[model]['Min Cost/Profit']
    
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=y_upper,
#         line_color='rgba(0,0,0,0)',
#         name=f'{model} average cost(+)/profit(-)',
#         showlegend=False,
#         legendgroup=f'{model}'
#     ))
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=y_lower,
#         fillcolor=colour_fills[i],
#         opacity=0.2,
#         line_color='rgba(0,0,0,0)',
#         name=f'{model} average cost(+)/profit(-)',
#         fill='tonexty',
#         showlegend=True,
#         legendgroup=f'{model}'
#     ))
#     subplot_fig.update_traces(mode='lines')
#     subplot_fig.add_trace(go.Scatter(
#         x=x, y=cost_profit[model]['Mean Cost/Profit'],
#         line_color=colour_lines[i], line_dash=dash_types[i],
#         name=f'{model} average cost(+)/profit(-)',
#         legendgroup=f'{model}',
#         showlegend=False,
#     ))
    subplot_fig.add_trace(go.Scatter(
        x=x, y=cost_profit[model]['Sum Cost/Profit'],
        line_color=colour_lines[i], line_dash=dash_types[0],
        name=f'{model} total cost(+)/profit(-)',
        legendgroup=f'{model} total',
        showlegend=True, line_width=line_widths[i],
        marker=dict(size=0, symbol=markers[i])
    ))
#     break
    
#     number_of_days = cost_predictions['Day'].max()+1
#     for day in range(number_of_days):
        
# number_of_days = cost_predictions['Day'].max()+1
# for day in range(number_of_days):
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model1'].loc[cost_profit_predictions['model1']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='blue',
#         line_color='blue'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model2'].loc[cost_profit_predictions['model2']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='green',
#         line_color='green'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model3'].loc[cost_profit_predictions['model3']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='red',
#         line_color='red'))
#     subplot_fig.add_trace(go.Box(
#         y=list(cost_profit_predictions['model4'].loc[cost_profit_predictions['model4']['Day']==day]['Cost/Profit']),
#         name=f"{day+1}", showlegend=False, boxmean='sd',
#         boxpoints=False, # only outliers
#         marker_color='dimgrey',
#         line_color='dimgrey'))

# y_lower = y_lower[::-1]
# subplot_fig.add_trace(go.Scatter(
#     x=x+x_rev,
#     y=y_upper+y_lower,
#     fill='tonextx',
#     fillcolor='rgba(0,176,246,0.2)',
#     line_color='rgba(0,0,0,1)',
#     name='Premium',
#     showlegend=False,))


# grid_power = grid_p[day]['Grid Power Value']
# # day_tariff = costs_predictions['Electricity Day Tariffs']


# subplot_fig.add_hline(y=ov['P_battery_MAX'][0], line_width=1.5, line_color="crimson", opacity=0.5,
#                       line_dash="dot", annotation_text="<i>MAX Battery Power</i>", 
#                       annotation_position="top left", annotation_font_size=12, annotation_font_color="crimson",
#                       annotation_opacity=0.5)

# subplot_fig.add_scatter(x=cost[day].index, y=battery_soc, line_shape='linear', name='Battery SOC', mode='lines+markers',
#                         marker=dict(size=4, symbol='square', line=dict(width=0), color='dimgrey', coloraxis='coloraxis'), line=dict(color='dimgrey'),
#                         showlegend=True, yaxis='y2', legendgroup='SOC')
# # # Electricity Day Tariff
# # subplot_fig.add_scatter(x=costs_predictions.index, y=day_tariff, line_shape='hv', name='Dnevna tarifa električne energije', mode='lines+markers',
# #                         marker=dict(size=0, symbol='circle', line=dict(width=0), color='teal', coloraxis='coloraxis'), line=dict(color='teal'),
# #                         showlegend=True, yaxis='y2', legendgroup='Day Tariff')

# subplot_fig.add_annotation(x=-0.08, y=0.5, text="<b>Power [kW]</b>", xanchor='left', yanchor='middle', textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
# subplot_fig.add_annotation(x=1.07, y=0.7, text="<b>State of Charge</b>", xanchor='left', yanchor='middle', textangle=-90, xref="paper", yref="paper", font_size=14, showarrow=False)
# subplot_fig.add_annotation(x=0.5, y=-0.1, text="<b>Timestep (Hour) in a Day</b>", textangle=0, xref="paper", yref="paper", font_size=14, showarrow=False)

# max_timestep = max(day_length, 100)
# # Prediction Power Values
# subplot_fig.update_layout(title="",
#                           yaxis=dict(title=''), barmode='overlay')
# subplot_fig.update_xaxes(tickformat='', griddash="dot", title='', range=[-0.4, day_length+0.4],
#                          tickvals=[i for i in range(0, max_timestep, 4)], 
#                          ticktext=[str(int(i/4)%24) for i in range(0, max_timestep, 4)], 
#                          showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2)

# # For plot export: w(1280)xh(720), w(1920)xh(1080)
# # For better overview in jupyter: w(850)xh(650)
plot_width = 980
plot_height = 950

# if model == 'model3' or model == 'model4':
#     max_p = max(grid_power.max(), pv_power.max(), total_ev_p.max(), battery_p.max(), battery_soc.max(), building_od.max())
# else:
#     max_p = max(grid_power.max(), pv_power.max(), total_ev_p.max(), battery_p.max(), battery_soc.max())

# power_margin = int(round(max_p/10)*10)+10
# power_ticks = int(power_margin/5)
# #     max_tariff = day_tariff.max()
# #     tariff_margin = int(max_tariff)+0.25

# subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman",
#                           title=dict(xanchor="center", x=0.5, font_size=24, y=0.99), 
#                           showlegend=True, coloraxis=dict(colorscale=[[0, 'crimson'], [0.5, 'lightgrey'], [1, 'grey']], 
#                                                           colorbar=dict(title=dict(text='', side='right'))), barmode='stack',
#                           legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'), scattermode='overlay',
#                           yaxis=dict(tickformat=" ,", range=[-power_margin, power_margin], dtick=power_ticks, showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2),
#                           yaxis2=dict(tickformat=" ,.0%", overlaying='y', anchor='free', nticks=11, dtick=0.05, 
#                                       tickmode='array', tickvals=[str(i/100) for i in range(0, 110, 25)], autoshift=True, 
#                                       shift=2, side='right', range=[-1.25, 1.25],
#                                       showspikes=True, spikecolor='black', spikedash='dot', spikethickness=-2))
# #                               yaxis3=dict(overlaying='y',
# #                                           range=[0, tariff_margin], visible=False))
subplot_fig.update_layout(height=plot_height, width=plot_width, font_family="Computer Modern Roman", 
                          scattermode='overlay', 
                          legend=dict(x=0.5, orientation='h', yanchor='bottom', entrywidth=0, y=1.02, xanchor='center'))

subplot_fig.show()
#     if not os.path.exists(f"plots/{model}/all_powers"):
#         os.mkdir(f"plots/{model}/all_powers")

#     subplot_fig.write_image(f"plots/{model}/all_powers/all_powers_day_{day}.png")

# del max_timestep, plot_width, plot_height